In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
import warnings
warnings.filterwarnings('ignore')
pd.options.display.max_columns = None
pd.options.display.max_rows = None
pd.options.display.float_format = '{:.6f}'.format
from sklearn.metrics import confusion_matrix,accuracy_score, f1_score, classification_report
from sklearn.metrics import roc_curve, roc_auc_score
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score,KFold

In [2]:
from sklearn.ensemble import AdaBoostClassifier, GradientBoostingClassifier
from xgboost import XGBClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import GaussianNB, BernoulliNB, MultinomialNB
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.pipeline import Pipeline
from sklearn.metrics import precision_score, recall_score, fbeta_score,make_scorer
from sklearn.model_selection import RandomizedSearchCV,StratifiedKFold
from catboost import CatBoostClassifier
from lightgbm import LGBMClassifier
from scipy.stats import randint as sp_randint
from scipy.stats import uniform as sp_uniform

In [3]:
df_new = pd.read_csv('no_show_new1.csv')

In [4]:
from sklearn.preprocessing import StandardScaler

df_num = df_new[['Age','Waitingperiod']]
df_cat = df_new.drop(['Age','Waitingperiod'],axis = 1)

ss = StandardScaler()

num_ss = ss.fit_transform(df_num)

df_num_ss = pd.DataFrame(num_ss, columns = df_num.columns)

df_new2 = pd.concat([df_num_ss, df_cat], axis = 1)

df_new2.head()

Age  Waitingperiod  Gender  Scholarship  Hipertension  Diabetes  \
0  0.763817      -0.715729       0     0.000000             1         0   
1  0.763817      -0.715729       1     0.000000             0         0   
2  1.027555      -0.715729       0     0.000000             0         0   
3 -1.346083      -0.715729       0     0.000000             0         0   
4  0.763817      -0.715729       0     0.000000             1         1   

   Alcoholism  Handcap  SMS_received  No-show  prior_appointments  \
0    0.000000 0.000000      0.000000        0            0.000000   
1    0.000000 0.000000      0.000000        0            1.000000   
2    0.000000 0.000000      0.000000        0            0.000000   
3    0.000000 0.000000      0.000000        0            1.000000   
4    0.000000 0.000000      0.000000        0            0.000000   

   regular_patient  prior_no_shows  Neighbourhood_Group1  \
0                0        0.000000                     0   
1                1        0.000000                     0   
2                0        0.000000                     1   
3                1        0.000000                     1   
4                0        0.000000                     0   

   Neighbourhood_Group2  Neighbourhood_Group3  Neighbourhood_Group4  \
0                     0                     1                     0   
1                     0                     1                     0   
2                     0                     0                     0   
3                     0                     0                     0   
4                     0                     1                     0   

   Neighbourhood_Group5  Neighbourhood_Group6  Neighbourhood_Group7  
0                     0                     0                     0  
1                     0                     0                     0  
2                     0                     0                     0  
3                     0                     0                     0  
4                     0                     0                     0

In [5]:
X = df_new2.drop('No-show', axis = 1)
y = df_new2['No-show']

X_train, X_test, y_train, y_test = train_test_split(X, y, random_state = 10, test_size = 0.3, stratify=y) 

In [6]:
def f2_func(y_true, y_pred):
    f2_score = fbeta_score(y_true, y_pred, beta=2)
    return f2_score

def my_f2_scorer():
    return make_scorer(f2_func)

In [7]:
params_lr = {'solver':['liblinear','newton-cg','lbfgs','sag','saga'],
          'penalty': ['none','l1','l2','elasticnet'],
         'C': [100,10,1.0,0.1,0.01]}

cv = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 42)

rsearch_lr = RandomizedSearchCV(estimator = LogisticRegression(), param_distributions = params_lr, n_iter = 100, cv = cv, scoring = my_f2_scorer(), random_state = 42)

rsearch_lr.fit(X_train, y_train)

RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
                   estimator=LogisticRegression(), n_iter=100,
                   param_distributions={'C': [100, 10, 1.0, 0.1, 0.01],
                                        'penalty': ['none', 'l1', 'l2',
                                                    'elasticnet'],
                                        'solver': ['liblinear', 'newton-cg',
                                                   'lbfgs', 'sag', 'saga']},
                   random_state=42, scoring=make_scorer(f2_func))

In [8]:
rsearch_lr.best_params_

{'solver': 'saga', 'penalty': 'none', 'C': 100}

In [9]:
lr_pipeline = Pipeline([
    ('lr_model', LogisticRegression(**rsearch_lr.best_params_))
])

In [10]:
params_dt = {'max_features':sp_randint(1,15),
          'max_depth': sp_randint(2,10),
         'min_samples_leaf': sp_randint(10,50),
         'criterion':['gini','entropy']}

cv = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 42)

rsearch_dt = RandomizedSearchCV(estimator = DecisionTreeClassifier(random_state = 42), param_distributions = params_dt, n_iter = 100, cv = cv, scoring = my_f2_scorer(), random_state = 42)

rsearch_dt.fit(X_train, y_train)

RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
                   estimator=DecisionTreeClassifier(random_state=42),
                   n_iter=100,
                   param_distributions={'criterion': ['gini', 'entropy'],
                                        'max_depth': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027F019A0B20>,
                                        'max_features': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027F019A8190>,
                                        'min_samples_leaf': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027F019AE820>},
                   random_state=42, scoring=make_scorer(f2_func))

In [11]:
rsearch_dt.best_params_

{'criterion': 'gini',
 'max_depth': 2,
 'max_features': 3,
 'min_samples_leaf': 46}

In [12]:
dt_pipeline = Pipeline([
    ('dt_model', DecisionTreeClassifier(**rsearch_dt.best_params_,random_state=42))
])

In [13]:
params_rf = {'n_estimators':sp_randint(50,150),
          'max_features':sp_randint(1,15),
          'max_depth': sp_randint(2,10),
         'min_samples_leaf': sp_randint(10,50),
         'criterion':['gini','entropy']}

cv = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 42)

rsearch_rf = RandomizedSearchCV(estimator = RandomForestClassifier(random_state = 42), param_distributions = params_rf, n_iter = 100, cv = cv, scoring = my_f2_scorer(), random_state = 42)

rsearch_rf.fit(X_train, y_train)

RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
                   estimator=RandomForestClassifier(random_state=42),
                   n_iter=100,
                   param_distributions={'criterion': ['gini', 'entropy'],
                                        'max_depth': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027F7BE05AF0>,
                                        'max_features': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027F018E20A0>,
                                        'min_samples_leaf': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027F018E93D0>,
                                        'n_estimators': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027F018ACBB0>},
                   random_state=42, scoring=make_scorer(f2_func))

In [14]:
rsearch_rf.best_params_

{'criterion': 'entropy',
 'max_depth': 2,
 'max_features': 14,
 'min_samples_leaf': 30,
 'n_estimators': 97}

In [15]:
rf_pipeline = Pipeline([
    ('rf_model', RandomForestClassifier(**rsearch_rf.best_params_,random_state=42))
])

In [16]:
gnb_pipeline = Pipeline([
    ('gnb_model', GaussianNB())
])

In [17]:
bnb_pipeline = Pipeline([
    ('bnb_model', BernoulliNB())
])

In [18]:
knn_pipeline = Pipeline([
    ('knn_model', KNeighborsClassifier())
])

In [19]:
params_ada = {'n_estimators':sp_randint(20,150),
          'learning_rate':[0.0001,0.001,0.01,0.1,1,2,3,4,5]}

cv = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 42)

rsearch_ada = RandomizedSearchCV(estimator = AdaBoostClassifier(random_state = 42), param_distributions = params_ada, n_iter = 100, cv = cv, scoring = my_f2_scorer(), random_state = 42)

rsearch_ada.fit(X_train, y_train)

RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
                   estimator=AdaBoostClassifier(random_state=42), n_iter=100,
                   param_distributions={'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1, 2, 3, 4, 5],
                                        'n_estimators': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027F019A8880>},
                   random_state=42, scoring=make_scorer(f2_func))

In [20]:
rsearch_ada.best_params_

{'learning_rate': 5, 'n_estimators': 70}

In [21]:
ada_pipeline = Pipeline([
    ('ada_model', AdaBoostClassifier(**rsearch_ada.best_params_, random_state = 42))
])

In [22]:
params_gb = {'n_estimators':sp_randint(50,200),
          'max_features':sp_randint(1,15),
          'max_depth': sp_randint(2,10),
         'learning_rate':[0.0001,0.001,0.01,0.1,1,2,3,4,5]}

cv = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 42)

rsearch_gb = RandomizedSearchCV(estimator = GradientBoostingClassifier(random_state = 42), param_distributions = params_gb, n_iter = 100, cv = cv, scoring = my_f2_scorer(), random_state = 42)

rsearch_gb.fit(X_train, y_train)

RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
                   estimator=GradientBoostingClassifier(random_state=42),
                   n_iter=100,
                   param_distributions={'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1, 2, 3, 4, 5],
                                        'max_depth': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027F051B43D0>,
                                        'max_features': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027F0518D8E0>,
                                        'n_estimators': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027F051ACFA0>},
                   random_state=42, scoring=make_scorer(f2_func))

In [23]:
rsearch_gb.best_params_

{'learning_rate': 5, 'max_depth': 4, 'max_features': 14, 'n_estimators': 170}

In [24]:
gb_pipeline = Pipeline([
    ('gb_model', GradientBoostingClassifier(**rsearch_gb.best_params_, random_state = 42))
])

In [25]:
params_cb = {'n_estimators':sp_randint(50,200),
          'max_depth': sp_randint(2,10),
         'learning_rate':[0.01,0.1,0.2,0.4,0.6,0.8,0.9]}

cv = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 42)

rsearch_cb = RandomizedSearchCV(estimator = CatBoostClassifier(random_state = 42), param_distributions = params_cb, n_iter = 100, cv = cv, scoring = my_f2_scorer(), random_state = 42)

rsearch_cb.fit(X_train, y_train)

0:	learn: 0.4518172	total: 183ms	remaining: 25.8s
1:	learn: 0.4191101	total: 186ms	remaining: 13s
2:	learn: 0.4090871	total: 189ms	remaining: 8.76s
3:	learn: 0.4054384	total: 192ms	remaining: 6.62s
4:	learn: 0.4046828	total: 195ms	remaining: 5.33s
5:	learn: 0.4037044	total: 197ms	remaining: 4.47s
6:	learn: 0.4034814	total: 200ms	remaining: 3.86s
7:	learn: 0.4031466	total: 203ms	remaining: 3.4s
8:	learn: 0.4028044	total: 205ms	remaining: 3.04s
9:	learn: 0.4022901	total: 208ms	remaining: 2.75s
10:	learn: 0.4021321	total: 211ms	remaining: 2.51s
11:	learn: 0.4017549	total: 214ms	remaining: 2.31s
12:	learn: 0.4015021	total: 216ms	remaining: 2.15s
13:	learn: 0.4010397	total: 219ms	remaining: 2s
14:	learn: 0.4006589	total: 222ms	remaining: 1.88s
15:	learn: 0.4003344	total: 225ms	remaining: 1.77s
16:	learn: 0.3999695	total: 227ms	remaining: 1.67s
17:	learn: 0.3996380	total: 230ms	remaining: 1.58s
18:	learn: 0.3992941	total: 233ms	remaining: 1.51s
19:	learn: 0.3989359	total: 236ms	remaining: 1.

65:	learn: 0.3921022	total: 177ms	remaining: 204ms
66:	learn: 0.3920436	total: 180ms	remaining: 201ms
67:	learn: 0.3920131	total: 182ms	remaining: 198ms
68:	learn: 0.3919648	total: 185ms	remaining: 195ms
69:	learn: 0.3917758	total: 187ms	remaining: 193ms
70:	learn: 0.3917108	total: 190ms	remaining: 190ms
71:	learn: 0.3916262	total: 192ms	remaining: 187ms
72:	learn: 0.3915454	total: 195ms	remaining: 184ms
73:	learn: 0.3915335	total: 197ms	remaining: 181ms
74:	learn: 0.3914816	total: 200ms	remaining: 178ms
75:	learn: 0.3913220	total: 202ms	remaining: 176ms
76:	learn: 0.3912117	total: 205ms	remaining: 173ms
77:	learn: 0.3911243	total: 208ms	remaining: 170ms
78:	learn: 0.3909297	total: 210ms	remaining: 168ms
79:	learn: 0.3908582	total: 213ms	remaining: 165ms
80:	learn: 0.3907390	total: 215ms	remaining: 162ms
81:	learn: 0.3907060	total: 218ms	remaining: 159ms
82:	learn: 0.3906217	total: 220ms	remaining: 157ms
83:	learn: 0.3904563	total: 223ms	remaining: 154ms
84:	learn: 0.3902307	total: 226

139:	learn: 0.3849997	total: 368ms	remaining: 5.26ms
140:	learn: 0.3848617	total: 371ms	remaining: 2.63ms
141:	learn: 0.3847614	total: 373ms	remaining: 0us
0:	learn: 0.4500618	total: 16.1ms	remaining: 2.28s
1:	learn: 0.4212206	total: 19.3ms	remaining: 1.35s
2:	learn: 0.4114445	total: 22.2ms	remaining: 1.03s
3:	learn: 0.4078232	total: 25ms	remaining: 864ms
4:	learn: 0.4061254	total: 27.7ms	remaining: 760ms
5:	learn: 0.4054133	total: 30.4ms	remaining: 688ms
6:	learn: 0.4050015	total: 33.1ms	remaining: 638ms
7:	learn: 0.4046545	total: 35.8ms	remaining: 600ms
8:	learn: 0.4042975	total: 38.4ms	remaining: 567ms
9:	learn: 0.4039211	total: 40.9ms	remaining: 540ms
10:	learn: 0.4036909	total: 43.7ms	remaining: 520ms
11:	learn: 0.4033280	total: 46.5ms	remaining: 504ms
12:	learn: 0.4027313	total: 49.5ms	remaining: 491ms
13:	learn: 0.4023526	total: 52.3ms	remaining: 478ms
14:	learn: 0.4020637	total: 55ms	remaining: 466ms
15:	learn: 0.4019150	total: 57.6ms	remaining: 453ms
16:	learn: 0.4012469	total

63:	learn: 0.3924433	total: 179ms	remaining: 218ms
64:	learn: 0.3924132	total: 181ms	remaining: 215ms
65:	learn: 0.3923210	total: 184ms	remaining: 211ms
66:	learn: 0.3921627	total: 186ms	remaining: 209ms
67:	learn: 0.3919960	total: 189ms	remaining: 206ms
68:	learn: 0.3918612	total: 191ms	remaining: 203ms
69:	learn: 0.3917093	total: 194ms	remaining: 200ms
70:	learn: 0.3916982	total: 196ms	remaining: 196ms
71:	learn: 0.3915563	total: 199ms	remaining: 194ms
72:	learn: 0.3914271	total: 202ms	remaining: 191ms
73:	learn: 0.3913867	total: 204ms	remaining: 188ms
74:	learn: 0.3913302	total: 207ms	remaining: 185ms
75:	learn: 0.3911699	total: 209ms	remaining: 182ms
76:	learn: 0.3911025	total: 212ms	remaining: 179ms
77:	learn: 0.3909565	total: 215ms	remaining: 176ms
78:	learn: 0.3908413	total: 217ms	remaining: 173ms
79:	learn: 0.3906223	total: 220ms	remaining: 170ms
80:	learn: 0.3905070	total: 222ms	remaining: 168ms
81:	learn: 0.3904472	total: 225ms	remaining: 165ms
82:	learn: 0.3902357	total: 227

0:	learn: 0.4497730	total: 2.82ms	remaining: 339ms
1:	learn: 0.4200939	total: 5.78ms	remaining: 344ms
2:	learn: 0.4123735	total: 8.11ms	remaining: 319ms
3:	learn: 0.4080313	total: 10.5ms	remaining: 308ms
4:	learn: 0.4065360	total: 12.8ms	remaining: 296ms
5:	learn: 0.4055754	total: 15.1ms	remaining: 289ms
6:	learn: 0.4051761	total: 17.3ms	remaining: 281ms
7:	learn: 0.4047576	total: 19.6ms	remaining: 276ms
8:	learn: 0.4044344	total: 22.1ms	remaining: 275ms
9:	learn: 0.4042971	total: 24.4ms	remaining: 271ms
10:	learn: 0.4040874	total: 26.8ms	remaining: 268ms
11:	learn: 0.4037964	total: 29.2ms	remaining: 265ms
12:	learn: 0.4031630	total: 31.5ms	remaining: 261ms
13:	learn: 0.4027803	total: 33.8ms	remaining: 258ms
14:	learn: 0.4024096	total: 36.2ms	remaining: 256ms
15:	learn: 0.4021539	total: 38.6ms	remaining: 254ms
16:	learn: 0.4018647	total: 41.1ms	remaining: 251ms
17:	learn: 0.4015746	total: 43.5ms	remaining: 249ms
18:	learn: 0.4014365	total: 45.8ms	remaining: 246ms
19:	learn: 0.4011229	t

...

75:	learn: 0.5002666	total: 173ms	remaining: 274ms
76:	learn: 0.4990422	total: 176ms	remaining: 272ms
77:	learn: 0.4977885	total: 178ms	remaining: 269ms
78:	learn: 0.4965454	total: 180ms	remaining: 267ms
79:	learn: 0.4953371	total: 182ms	remaining: 265ms
80:	learn: 0.4941270	total: 185ms	remaining: 262ms
81:	learn: 0.4929394	total: 187ms	remaining: 260ms
82:	learn: 0.4917923	total: 189ms	remaining: 258ms
83:	learn: 0.4906818	total: 192ms	remaining: 256ms
84:	learn: 0.4895923	total: 194ms	remaining: 253ms
85:	learn: 0.4885065	total: 196ms	remaining: 251ms
86:	learn: 0.4874471	total: 198ms	remaining: 249ms
87:	learn: 0.4863457	total: 201ms	remaining: 246ms
88:	learn: 0.4853252	total: 203ms	remaining: 244ms
89:	learn: 0.4842674	total: 205ms	remaining: 242ms
90:	learn: 0.4832460	total: 207ms	remaining: 239ms
91:	learn: 0.4822276	total: 210ms	remaining: 237ms
92:	learn: 0.4812397	total: 212ms	remaining: 235ms
93:	learn: 0.4802891	total: 214ms	remaining: 232ms
94:	learn: 0.4793141	total: 216

79:	learn: 0.4951805	total: 182ms	remaining: 264ms
80:	learn: 0.4939900	total: 184ms	remaining: 262ms
81:	learn: 0.4928046	total: 187ms	remaining: 259ms
82:	learn: 0.4916587	total: 189ms	remaining: 257ms
83:	learn: 0.4905116	total: 191ms	remaining: 255ms
84:	learn: 0.4894015	total: 193ms	remaining: 252ms
85:	learn: 0.4883073	total: 195ms	remaining: 250ms
86:	learn: 0.4872318	total: 198ms	remaining: 247ms
87:	learn: 0.4861321	total: 200ms	remaining: 245ms
88:	learn: 0.4851365	total: 202ms	remaining: 243ms
89:	learn: 0.4840780	total: 204ms	remaining: 241ms
90:	learn: 0.4830585	total: 207ms	remaining: 238ms
91:	learn: 0.4820606	total: 209ms	remaining: 236ms
92:	learn: 0.4810776	total: 211ms	remaining: 234ms
93:	learn: 0.4801298	total: 213ms	remaining: 231ms
94:	learn: 0.4791536	total: 216ms	remaining: 229ms
95:	learn: 0.4782153	total: 218ms	remaining: 227ms
96:	learn: 0.4772768	total: 220ms	remaining: 224ms
97:	learn: 0.4763333	total: 222ms	remaining: 222ms
98:	learn: 0.4754185	total: 224

78:	learn: 0.4962153	total: 181ms	remaining: 268ms
79:	learn: 0.4950044	total: 183ms	remaining: 265ms
80:	learn: 0.4938112	total: 185ms	remaining: 263ms
81:	learn: 0.4926251	total: 187ms	remaining: 261ms
82:	learn: 0.4914804	total: 190ms	remaining: 258ms
83:	learn: 0.4903726	total: 192ms	remaining: 256ms
84:	learn: 0.4892635	total: 194ms	remaining: 254ms
85:	learn: 0.4881480	total: 196ms	remaining: 251ms
86:	learn: 0.4870690	total: 199ms	remaining: 249ms
87:	learn: 0.4859672	total: 201ms	remaining: 247ms
88:	learn: 0.4849683	total: 203ms	remaining: 244ms
89:	learn: 0.4839113	total: 205ms	remaining: 242ms
90:	learn: 0.4828920	total: 207ms	remaining: 239ms
91:	learn: 0.4818728	total: 210ms	remaining: 237ms
92:	learn: 0.4808915	total: 212ms	remaining: 235ms
93:	learn: 0.4799414	total: 214ms	remaining: 233ms
94:	learn: 0.4789616	total: 217ms	remaining: 230ms
95:	learn: 0.4780226	total: 219ms	remaining: 228ms
96:	learn: 0.4770820	total: 221ms	remaining: 225ms
97:	learn: 0.4761371	total: 223

45:	learn: 0.3781735	total: 782ms	remaining: 2.5s
46:	learn: 0.3773099	total: 798ms	remaining: 2.48s
47:	learn: 0.3768580	total: 812ms	remaining: 2.45s
48:	learn: 0.3764050	total: 828ms	remaining: 2.43s
49:	learn: 0.3761854	total: 843ms	remaining: 2.41s
50:	learn: 0.3757986	total: 859ms	remaining: 2.39s
51:	learn: 0.3754071	total: 874ms	remaining: 2.37s
52:	learn: 0.3750224	total: 889ms	remaining: 2.35s
53:	learn: 0.3744845	total: 904ms	remaining: 2.33s
54:	learn: 0.3738915	total: 920ms	remaining: 2.31s
55:	learn: 0.3734714	total: 928ms	remaining: 2.27s
56:	learn: 0.3731185	total: 951ms	remaining: 2.27s
57:	learn: 0.3726683	total: 966ms	remaining: 2.25s
58:	learn: 0.3723430	total: 981ms	remaining: 2.23s
59:	learn: 0.3722787	total: 996ms	remaining: 2.21s
60:	learn: 0.3719512	total: 1.01s	remaining: 2.19s
61:	learn: 0.3716282	total: 1.02s	remaining: 2.15s
62:	learn: 0.3712763	total: 1.04s	remaining: 2.15s
63:	learn: 0.3710426	total: 1.06s	remaining: 2.13s
64:	learn: 0.3706823	total: 1.07

RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
                   estimator=<catboost.core.CatBoostClassifier object at 0x0000027F018ACA30>,
                   n_iter=100,
                   param_distributions={'learning_rate': [0.01, 0.1, 0.2, 0.4,
                                                          0.6, 0.8, 0.9],
                                        'max_depth': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027F051AC1F0>,
                                        'n_estimators': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027F01956BE0>},
                   random_state=42, scoring=make_scorer(f2_func))

In [26]:
rsearch_cb.best_params_

{'learning_rate': 0.9, 'max_depth': 9, 'n_estimators': 193}

In [27]:
cb_pipeline = Pipeline([
    ('cb_model', CatBoostClassifier(**rsearch_cb.best_params_, random_state = 42))
])

In [28]:
params_lgbm = {'n_estimators':sp_randint(50,200),
          'num_leaves':sp_randint(2,50),
          'max_depth': sp_randint(2,10),
         'learning_rate':[0.0001,0.001,0.01,0.1,1,2,3,4,5]}

cv = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 42)

rsearch_lgbm = RandomizedSearchCV(estimator = LGBMClassifier(random_state = 42), param_distributions = params_lgbm, n_iter = 100, cv = cv, scoring = my_f2_scorer(), random_state = 42)

rsearch_lgbm.fit(X_train, y_train)

RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
                   estimator=LGBMClassifier(random_state=42), n_iter=100,
                   param_distributions={'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1, 2, 3, 4, 5],
                                        'max_depth': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027F052050A0>,
                                        'n_estimators': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027F052059D0>,
                                        'num_leaves': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000027F019664C0>},
                   random_state=42, scoring=make_scorer(f2_func))

In [29]:
rsearch_lgbm.best_params_

{'learning_rate': 3, 'max_depth': 2, 'n_estimators': 121, 'num_leaves': 13}

In [30]:
lgbm_pipeline = Pipeline([
    ('lgbm_model', LGBMClassifier(**rsearch_lgbm.best_params_, random_state = 42))
])

In [31]:
params_xgb = {'gamma':sp_randint(0,5),
          'max_depth': sp_randint(2,10),
         'learning_rate':[0.0001,0.001,0.01,0.1,1,2,3,4,5]}

cv = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 42)

rsearch_xgb = RandomizedSearchCV(estimator = XGBClassifier(random_state = 42), param_distributions = params_xgb, n_iter = 100, cv = cv, scoring = my_f2_scorer(), random_state = 42)

rsearch_xgb.fit(X_train, y_train)

RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
                   estimator=XGBClassifier(base_score=None, booster=None,
                                           callbacks=None,
                                           colsample_bylevel=None,
                                           colsample_bynode=None,
                                           colsample_bytree=None,
                                           early_stopping_rounds=None,
                                           enable_categorical=False,
                                           eval_metric=None, gamma=None,
                                           gpu_id=None, grow_policy=None,
                                           importance_type=None,
                                           intera...
                                           predictor=None, random_state=42,
                                           reg_alpha=None, reg_lambda=None, ...),
                   n_it

In [32]:
rsearch_xgb.best_params_

{'gamma': 1, 'learning_rate': 3, 'max_depth': 8}

In [33]:
xgb_pipeline = Pipeline([
    ('xgb_model', XGBClassifier(**rsearch_xgb.best_params_, random_state = 42))
])

In [34]:
pipe_all = [lr_pipeline, dt_pipeline, rf_pipeline, gnb_pipeline, bnb_pipeline, ada_pipeline, gb_pipeline, xgb_pipeline, cb_pipeline, lgbm_pipeline,
            knn_pipeline]

for pipe in pipe_all:
  pipe.fit(X_train, y_train)

0:	learn: 0.4499831	total: 12.6ms	remaining: 2.42s
1:	learn: 0.4137693	total: 31.1ms	remaining: 2.97s
2:	learn: 0.4067001	total: 43.6ms	remaining: 2.76s
3:	learn: 0.4046764	total: 51.2ms	remaining: 2.42s
4:	learn: 0.4032107	total: 62.2ms	remaining: 2.34s
5:	learn: 0.4021759	total: 93.2ms	remaining: 2.9s
6:	learn: 0.4010207	total: 109ms	remaining: 2.89s
7:	learn: 0.4003929	total: 125ms	remaining: 2.88s
8:	learn: 0.3998047	total: 141ms	remaining: 2.87s
9:	learn: 0.3995003	total: 167ms	remaining: 3.05s
10:	learn: 0.3987932	total: 187ms	remaining: 3.1s
11:	learn: 0.3983008	total: 218ms	remaining: 3.28s
12:	learn: 0.3974524	total: 234ms	remaining: 3.23s
13:	learn: 0.3968217	total: 249ms	remaining: 3.18s
14:	learn: 0.3959050	total: 264ms	remaining: 3.13s
15:	learn: 0.3951858	total: 280ms	remaining: 3.09s
16:	learn: 0.3943838	total: 295ms	remaining: 3.06s
17:	learn: 0.3939009	total: 326ms	remaining: 3.17s
18:	learn: 0.3932177	total: 334ms	remaining: 3.05s
19:	learn: 0.3921768	total: 357ms	rem

161:	learn: 0.3426507	total: 2.94s	remaining: 563ms
162:	learn: 0.3426165	total: 2.96s	remaining: 544ms
163:	learn: 0.3426041	total: 2.97s	remaining: 526ms
164:	learn: 0.3425940	total: 2.99s	remaining: 507ms
165:	learn: 0.3424148	total: 3s	remaining: 489ms
166:	learn: 0.3421738	total: 3.02s	remaining: 470ms
167:	learn: 0.3420370	total: 3.04s	remaining: 452ms
168:	learn: 0.3418874	total: 3.05s	remaining: 433ms
169:	learn: 0.3417930	total: 3.08s	remaining: 417ms
170:	learn: 0.3414981	total: 3.1s	remaining: 398ms
171:	learn: 0.3413169	total: 3.13s	remaining: 382ms
172:	learn: 0.3411503	total: 3.14s	remaining: 363ms
173:	learn: 0.3411487	total: 3.17s	remaining: 346ms
174:	learn: 0.3410197	total: 3.19s	remaining: 328ms
175:	learn: 0.3409102	total: 3.2s	remaining: 310ms
176:	learn: 0.3406306	total: 3.22s	remaining: 291ms
177:	learn: 0.3405621	total: 3.23s	remaining: 273ms
178:	learn: 0.3405315	total: 3.25s	remaining: 254ms
179:	learn: 0.3403066	total: 3.27s	remaining: 236ms
180:	learn: 0.340

In [35]:
model_scores = {"Model Name" : [], 'Accuracy train': [], 'Precision train': [], 'Recall train': [], 'F1 train': [], 
                'F1 Avg Weighted train': [], 'F2 train': [],'ROC AUC train': [], 'Accuracy test': [], 'Precision test': [], 
                'Recall test': [], 'F1 test': [], 'F1 Avg Weighted test': [], 'F2 test': [],'ROC AUC test': [], 
                'CV-5-Mean': [], 'CV-5-SD': []}

for model in pipe_all:
    
    model_scores['Model Name'].append(str(model[0]).split('(')[0])
    
    model_scores['Accuracy train'].append(model.score(X_train, y_train))
    pred_tr = model.predict(X_train)
    prob_tr = model.predict_proba(X_train)[:,1]
    model_scores['Precision train'].append(precision_score(y_train, pred_tr))
    model_scores['Recall train'].append(recall_score(y_train, pred_tr))
    model_scores['F1 train'].append(f1_score(y_train, pred_tr))
    model_scores['F1 Avg Weighted train'].append(f1_score(y_train, pred_tr, average = 'weighted'))
    model_scores['F2 train'].append(fbeta_score(y_train, pred_tr, beta = 2.0))
    model_scores['ROC AUC train'].append(roc_auc_score(y_train, prob_tr))
    
    model_scores['Accuracy test'].append(model.score(X_test, y_test))
    pred_ts = model.predict(X_test)
    prob_ts = model.predict_proba(X_test)[:,1]
    model_scores['Precision test'].append(precision_score(y_test, pred_ts))
    model_scores['Recall test'].append(recall_score(y_test, pred_ts))
    model_scores['F1 test'].append(f1_score(y_test, pred_ts))
    model_scores['F1 Avg Weighted test'].append(f1_score(y_test, pred_ts, average = 'weighted'))
    model_scores['F2 test'].append(fbeta_score(y_test, pred_ts, beta = 2.0))
    model_scores['ROC AUC test'].append(roc_auc_score(y_test, prob_ts))

    model_scores['CV-5-Mean'].append(cross_val_score(model,X_train,y_train,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring=my_f2_scorer()).mean())
    model_scores['CV-5-SD'].append(cross_val_score(model,X_train,y_train,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring=my_f2_scorer()).std())

0:	learn: 0.4501238	total: 6.96ms	remaining: 1.34s
1:	learn: 0.4128696	total: 41.4ms	remaining: 3.95s
2:	learn: 0.4052068	total: 56.4ms	remaining: 3.57s
3:	learn: 0.4018865	total: 71.6ms	remaining: 3.38s
4:	learn: 0.4004011	total: 78.6ms	remaining: 2.96s
5:	learn: 0.3997675	total: 102ms	remaining: 3.18s
6:	learn: 0.3992549	total: 117ms	remaining: 3.11s
7:	learn: 0.3980699	total: 124ms	remaining: 2.87s
8:	learn: 0.3975456	total: 131ms	remaining: 2.68s
9:	learn: 0.3971286	total: 147ms	remaining: 2.69s
10:	learn: 0.3959120	total: 163ms	remaining: 2.69s
11:	learn: 0.3946020	total: 178ms	remaining: 2.68s
12:	learn: 0.3935389	total: 194ms	remaining: 2.68s
13:	learn: 0.3920660	total: 209ms	remaining: 2.67s
14:	learn: 0.3913695	total: 224ms	remaining: 2.65s
15:	learn: 0.3906713	total: 239ms	remaining: 2.65s
16:	learn: 0.3901610	total: 254ms	remaining: 2.63s
17:	learn: 0.3893191	total: 261ms	remaining: 2.54s
18:	learn: 0.3884722	total: 285ms	remaining: 2.61s
19:	learn: 0.3876837	total: 292ms	re

171:	learn: 0.3322011	total: 2.62s	remaining: 320ms
172:	learn: 0.3319613	total: 2.63s	remaining: 304ms
173:	learn: 0.3316408	total: 2.65s	remaining: 289ms
174:	learn: 0.3313876	total: 2.67s	remaining: 274ms
175:	learn: 0.3310319	total: 2.67s	remaining: 258ms
176:	learn: 0.3307252	total: 2.7s	remaining: 244ms
177:	learn: 0.3303118	total: 2.73s	remaining: 230ms
178:	learn: 0.3299482	total: 2.74s	remaining: 215ms
179:	learn: 0.3296947	total: 2.76s	remaining: 199ms
180:	learn: 0.3291957	total: 2.77s	remaining: 184ms
181:	learn: 0.3288114	total: 2.79s	remaining: 169ms
182:	learn: 0.3285087	total: 2.8s	remaining: 153ms
183:	learn: 0.3279623	total: 2.82s	remaining: 138ms
184:	learn: 0.3276910	total: 2.83s	remaining: 123ms
185:	learn: 0.3272187	total: 2.84s	remaining: 107ms
186:	learn: 0.3268174	total: 2.87s	remaining: 92ms
187:	learn: 0.3266184	total: 2.88s	remaining: 76.6ms
188:	learn: 0.3264480	total: 2.9s	remaining: 61.3ms
189:	learn: 0.3263077	total: 2.91s	remaining: 46ms
190:	learn: 0.3

145:	learn: 0.3382631	total: 2.15s	remaining: 691ms
146:	learn: 0.3381837	total: 2.17s	remaining: 679ms
147:	learn: 0.3380014	total: 2.18s	remaining: 662ms
148:	learn: 0.3377851	total: 2.18s	remaining: 645ms
149:	learn: 0.3373909	total: 2.2s	remaining: 630ms
150:	learn: 0.3369946	total: 2.21s	remaining: 616ms
151:	learn: 0.3366676	total: 2.22s	remaining: 599ms
152:	learn: 0.3361360	total: 2.24s	remaining: 587ms
153:	learn: 0.3359460	total: 2.25s	remaining: 570ms
154:	learn: 0.3354148	total: 2.27s	remaining: 558ms
155:	learn: 0.3352571	total: 2.28s	remaining: 541ms
156:	learn: 0.3347605	total: 2.29s	remaining: 525ms
157:	learn: 0.3345784	total: 2.3s	remaining: 511ms
158:	learn: 0.3342661	total: 2.32s	remaining: 496ms
159:	learn: 0.3340442	total: 2.33s	remaining: 482ms
160:	learn: 0.3336192	total: 2.35s	remaining: 467ms
161:	learn: 0.3333447	total: 2.36s	remaining: 451ms
162:	learn: 0.3331089	total: 2.37s	remaining: 435ms
163:	learn: 0.3327660	total: 2.38s	remaining: 421ms
164:	learn: 0.

115:	learn: 0.3474242	total: 1.59s	remaining: 1.06s
116:	learn: 0.3469986	total: 1.6s	remaining: 1.04s
117:	learn: 0.3468216	total: 1.62s	remaining: 1.03s
118:	learn: 0.3466736	total: 1.63s	remaining: 1.01s
119:	learn: 0.3463451	total: 1.65s	remaining: 1s
120:	learn: 0.3461147	total: 1.66s	remaining: 990ms
121:	learn: 0.3457754	total: 1.67s	remaining: 973ms
122:	learn: 0.3453329	total: 1.69s	remaining: 964ms
123:	learn: 0.3450452	total: 1.71s	remaining: 951ms
124:	learn: 0.3445346	total: 1.72s	remaining: 934ms
125:	learn: 0.3441794	total: 1.74s	remaining: 925ms
126:	learn: 0.3438292	total: 1.75s	remaining: 908ms
127:	learn: 0.3436353	total: 1.77s	remaining: 901ms
128:	learn: 0.3432237	total: 1.79s	remaining: 886ms
129:	learn: 0.3430983	total: 1.8s	remaining: 873ms
130:	learn: 0.3430097	total: 1.82s	remaining: 860ms
131:	learn: 0.3427984	total: 1.82s	remaining: 843ms
132:	learn: 0.3425148	total: 1.83s	remaining: 827ms
133:	learn: 0.3422840	total: 1.84s	remaining: 811ms
134:	learn: 0.341

82:	learn: 0.3618366	total: 1.21s	remaining: 1.61s
83:	learn: 0.3614505	total: 1.22s	remaining: 1.58s
84:	learn: 0.3612292	total: 1.23s	remaining: 1.56s
85:	learn: 0.3610173	total: 1.24s	remaining: 1.55s
86:	learn: 0.3606661	total: 1.26s	remaining: 1.54s
87:	learn: 0.3602244	total: 1.28s	remaining: 1.52s
88:	learn: 0.3599309	total: 1.29s	remaining: 1.51s
89:	learn: 0.3595528	total: 1.31s	remaining: 1.5s
90:	learn: 0.3592455	total: 1.31s	remaining: 1.47s
91:	learn: 0.3587676	total: 1.34s	remaining: 1.47s
92:	learn: 0.3584380	total: 1.34s	remaining: 1.45s
93:	learn: 0.3579106	total: 1.37s	remaining: 1.44s
94:	learn: 0.3571777	total: 1.38s	remaining: 1.42s
95:	learn: 0.3567442	total: 1.4s	remaining: 1.41s
96:	learn: 0.3560806	total: 1.41s	remaining: 1.39s
97:	learn: 0.3555698	total: 1.43s	remaining: 1.39s
98:	learn: 0.3553922	total: 1.45s	remaining: 1.37s
99:	learn: 0.3550711	total: 1.45s	remaining: 1.35s
100:	learn: 0.3548268	total: 1.48s	remaining: 1.34s
101:	learn: 0.3545257	total: 1.4

...

0:	learn: 0.4507408	total: 23ms	remaining: 4.41s
1:	learn: 0.4125704	total: 30.3ms	remaining: 2.89s
2:	learn: 0.4066546	total: 39.8ms	remaining: 2.52s
3:	learn: 0.4029390	total: 56ms	remaining: 2.65s
4:	learn: 0.4012460	total: 70.4ms	remaining: 2.65s
5:	learn: 0.4002442	total: 77.8ms	remaining: 2.42s
6:	learn: 0.3994224	total: 117ms	remaining: 3.11s
7:	learn: 0.3984744	total: 125ms	remaining: 2.88s
8:	learn: 0.3977132	total: 149ms	remaining: 3.04s
9:	learn: 0.3970133	total: 163ms	remaining: 2.98s
10:	learn: 0.3962166	total: 179ms	remaining: 2.96s
11:	learn: 0.3950276	total: 193ms	remaining: 2.91s
12:	learn: 0.3934832	total: 209ms	remaining: 2.89s
13:	learn: 0.3923394	total: 223ms	remaining: 2.86s
14:	learn: 0.3916292	total: 239ms	remaining: 2.83s
15:	learn: 0.3908801	total: 254ms	remaining: 2.81s
16:	learn: 0.3897143	total: 286ms	remaining: 2.96s
17:	learn: 0.3889627	total: 293ms	remaining: 2.85s
18:	learn: 0.3879252	total: 316ms	remaining: 2.9s
19:	learn: 0.3869279	total: 324ms	remain

162:	learn: 0.3331089	total: 2.36s	remaining: 435ms
163:	learn: 0.3327660	total: 2.38s	remaining: 420ms
164:	learn: 0.3324068	total: 2.38s	remaining: 405ms
165:	learn: 0.3320986	total: 2.41s	remaining: 392ms
166:	learn: 0.3317405	total: 2.42s	remaining: 376ms
167:	learn: 0.3316911	total: 2.42s	remaining: 361ms
168:	learn: 0.3314943	total: 2.44s	remaining: 346ms
169:	learn: 0.3313751	total: 2.45s	remaining: 332ms
170:	learn: 0.3312316	total: 2.48s	remaining: 320ms
171:	learn: 0.3310535	total: 2.5s	remaining: 305ms
172:	learn: 0.3308097	total: 2.51s	remaining: 290ms
173:	learn: 0.3304775	total: 2.53s	remaining: 276ms
174:	learn: 0.3303894	total: 2.54s	remaining: 261ms
175:	learn: 0.3302288	total: 2.56s	remaining: 247ms
176:	learn: 0.3299591	total: 2.58s	remaining: 233ms
177:	learn: 0.3295928	total: 2.59s	remaining: 218ms
178:	learn: 0.3293072	total: 2.6s	remaining: 203ms
179:	learn: 0.3289896	total: 2.62s	remaining: 189ms
180:	learn: 0.3287356	total: 2.63s	remaining: 174ms
181:	learn: 0.

136:	learn: 0.3411874	total: 1.94s	remaining: 794ms
137:	learn: 0.3407617	total: 1.95s	remaining: 777ms
138:	learn: 0.3403162	total: 1.97s	remaining: 767ms
139:	learn: 0.3400399	total: 1.98s	remaining: 750ms
140:	learn: 0.3398870	total: 2s	remaining: 739ms
141:	learn: 0.3398303	total: 2.01s	remaining: 722ms
142:	learn: 0.3395520	total: 2.03s	remaining: 710ms
143:	learn: 0.3390348	total: 2.04s	remaining: 694ms
144:	learn: 0.3386051	total: 2.06s	remaining: 684ms
145:	learn: 0.3380426	total: 2.08s	remaining: 670ms
146:	learn: 0.3376754	total: 2.09s	remaining: 653ms
147:	learn: 0.3371928	total: 2.11s	remaining: 642ms
148:	learn: 0.3369890	total: 2.13s	remaining: 628ms
149:	learn: 0.3366923	total: 2.14s	remaining: 614ms
150:	learn: 0.3364131	total: 2.16s	remaining: 600ms
151:	learn: 0.3360170	total: 2.16s	remaining: 584ms
152:	learn: 0.3358312	total: 2.19s	remaining: 572ms
153:	learn: 0.3355802	total: 2.19s	remaining: 556ms
154:	learn: 0.3352342	total: 2.22s	remaining: 544ms
155:	learn: 0.3

108:	learn: 0.3523191	total: 1.6s	remaining: 1.23s
109:	learn: 0.3520919	total: 1.6s	remaining: 1.21s
110:	learn: 0.3518624	total: 1.62s	remaining: 1.2s
111:	learn: 0.3514064	total: 1.65s	remaining: 1.19s
112:	learn: 0.3511396	total: 1.67s	remaining: 1.18s
113:	learn: 0.3506663	total: 1.68s	remaining: 1.16s
114:	learn: 0.3500604	total: 1.69s	remaining: 1.15s
115:	learn: 0.3495699	total: 1.71s	remaining: 1.14s
116:	learn: 0.3491008	total: 1.72s	remaining: 1.12s
117:	learn: 0.3488136	total: 1.74s	remaining: 1.11s
118:	learn: 0.3484719	total: 1.75s	remaining: 1.09s
119:	learn: 0.3481720	total: 1.79s	remaining: 1.09s
120:	learn: 0.3478999	total: 1.8s	remaining: 1.07s
121:	learn: 0.3477663	total: 1.82s	remaining: 1.06s
122:	learn: 0.3472613	total: 1.83s	remaining: 1.04s
123:	learn: 0.3469160	total: 1.85s	remaining: 1.03s
124:	learn: 0.3465714	total: 1.86s	remaining: 1.01s
125:	learn: 0.3459461	total: 1.88s	remaining: 999ms
126:	learn: 0.3455074	total: 1.89s	remaining: 981ms
127:	learn: 0.34

82:	learn: 0.3597334	total: 1.25s	remaining: 1.66s
83:	learn: 0.3592620	total: 1.27s	remaining: 1.65s
84:	learn: 0.3592564	total: 1.27s	remaining: 1.62s
85:	learn: 0.3590083	total: 1.31s	remaining: 1.64s
86:	learn: 0.3586369	total: 1.32s	remaining: 1.61s
87:	learn: 0.3582795	total: 1.34s	remaining: 1.6s
88:	learn: 0.3580574	total: 1.35s	remaining: 1.58s
89:	learn: 0.3574837	total: 1.38s	remaining: 1.57s
90:	learn: 0.3571572	total: 1.38s	remaining: 1.55s
91:	learn: 0.3569136	total: 1.41s	remaining: 1.54s
92:	learn: 0.3566022	total: 1.41s	remaining: 1.52s
93:	learn: 0.3560148	total: 1.44s	remaining: 1.51s
94:	learn: 0.3557018	total: 1.44s	remaining: 1.49s
95:	learn: 0.3552765	total: 1.47s	remaining: 1.48s
96:	learn: 0.3549054	total: 1.47s	remaining: 1.46s
97:	learn: 0.3545863	total: 1.5s	remaining: 1.45s
98:	learn: 0.3543450	total: 1.5s	remaining: 1.43s
99:	learn: 0.3541570	total: 1.53s	remaining: 1.42s
100:	learn: 0.3538907	total: 1.53s	remaining: 1.4s
101:	learn: 0.3536972	total: 1.56s

In [36]:
pd.DataFrame(model_scores).round(4)

Model Name  Accuracy train  \
0                                  LogisticRegression        0.819900   
1                              DecisionTreeClassifier        0.811700   
2                              RandomForestClassifier        0.825000   
3                                          GaussianNB        0.791100   
4                                         BernoulliNB        0.819500   
5                                  AdaBoostClassifier        0.201900   
6                          GradientBoostingClassifier        0.276200   
7                                       XGBClassifier        0.754400   
8   <catboost.core.CatBoostClassifier object at 0x...        0.859400   
9                                      LGBMClassifier        0.574300   
10                               KNeighborsClassifier        0.850200   

    Precision train  Recall train  F1 train  F1 Avg Weighted train  F2 train  \
0          0.758000      0.158800  0.262600               0.769200  0.188600   
1          0.564400      0.296500  0.388800               0.787800  0.327600   
2          0.691800      0.240800  0.357200               0.789400  0.276900   
3          0.472400      0.292600  0.361400               0.771400  0.316700   
4          0.685800      0.195700  0.304600               0.776800  0.228400   
5          0.201900      1.000000  0.336000               0.067900  0.558500   
6          0.203400      0.886300  0.330900               0.235800  0.530300   
7          0.398900      0.426000  0.412000               0.757400  0.420300   
8          0.839100      0.375500  0.518900               0.837100  0.422200   
9          0.290000      0.764900  0.420500               0.614500  0.576200   
10         0.737300      0.401400  0.519800               0.832200  0.441600   

    ROC AUC train  Accuracy test  Precision test  Recall test  F1 test  \
0        0.740900       0.818300        0.750200     0.150200 0.250300   
1        0.643600       0.809200        0.553400     0.285400 0.376600   
2        0.746500       0.823100        0.682300     0.231900 0.346200   
3        0.697800       0.789500        0.465800     0.289300 0.356900   
4        0.713700       0.817200        0.671900     0.185600 0.290900   
5        0.619300       0.201900        0.201900     1.000000 0.336000   
6        0.504000       0.275200        0.202600     0.882300 0.329600   
7        0.631700       0.753900        0.396900     0.420700 0.408500   
8        0.862600       0.816900        0.608900     0.260500 0.364900   
9        0.643800       0.575000        0.291600     0.773000 0.423500   
10       0.870100       0.803600        0.526500     0.274900 0.361200   

    F1 Avg Weighted test  F2 test  ROC AUC test  CV-5-Mean  CV-5-SD  
0               0.766100 0.178800      0.739800   0.188500 0.004900  
1               0.784200 0.316000      0.636000   0.327600 0.009900  
2               0.786300 0.267200      0.744900   0.280600 0.007500  
3               0.769700 0.313000      0.696500   0.314100 0.005300  
4               0.773100 0.217000      0.712800   0.228500 0.009900  
5               0.067900 0.558500      0.613600   0.558500 0.003900  
6               0.235000 0.528100      0.501900   0.442700 0.049100  
7               0.756600 0.415700      0.629600   0.238100 0.158500  
8               0.786400 0.294100      0.755700   0.313300 0.004400  
9               0.615000 0.581100      0.646700   0.566800 0.023000  
10              0.778400 0.304000      0.687200   0.299600 0.007200

In [37]:
from imblearn.over_sampling import SMOTE
from collections import Counter

counter = Counter(y_train)
print('Before', counter)

smt = SMOTE(random_state=10)
X_train_sm, y_train_sm = smt.fit_resample(X_train, y_train)

counter = Counter(y_train_sm)
print('After', counter)

Before Counter({0: 61743, 1: 15623})
After Counter({0: 61743, 1: 61743})


In [38]:
lr_pipeline = Pipeline([
    ('lr_model', LogisticRegression(**rsearch_lr.best_params_))
])

In [39]:
dt_pipeline = Pipeline([
    ('dt_model', DecisionTreeClassifier(**rsearch_dt.best_params_,random_state=42))
])

In [40]:
rf_pipeline = Pipeline([
    ('rf_model', RandomForestClassifier(**rsearch_rf.best_params_,random_state=42))
])

In [41]:
gnb_pipeline = Pipeline([
    ('gnb_model', GaussianNB())
])

In [42]:
bnb_pipeline = Pipeline([
    ('bnb_model', BernoulliNB())
])

In [43]:
knn_pipeline = Pipeline([
    ('knn_model', KNeighborsClassifier())
])

In [44]:
ada_pipeline = Pipeline([
    ('ada_model', AdaBoostClassifier(**rsearch_ada.best_params_, random_state = 42))
])

In [45]:
gb_pipeline = Pipeline([
    ('gb_model', GradientBoostingClassifier(**rsearch_gb.best_params_, random_state = 42))
])

In [46]:
cb_pipeline = Pipeline([
    ('cb_model', CatBoostClassifier(**rsearch_cb.best_params_, random_state = 42))
])

In [47]:
lgbm_pipeline = Pipeline([
    ('lgbm_model', LGBMClassifier(**rsearch_lgbm.best_params_, random_state = 42))
])

In [48]:
xgb_pipeline = Pipeline([
    ('xgb_model', XGBClassifier(**rsearch_xgb.best_params_, random_state = 42))
])

In [49]:
pipe_all = [lr_pipeline, dt_pipeline, rf_pipeline, gnb_pipeline, bnb_pipeline, ada_pipeline, gb_pipeline, xgb_pipeline, cb_pipeline, lgbm_pipeline,
            knn_pipeline]
            
for pipe in pipe_all:
  pipe.fit(X_train_sm, y_train_sm)

0:	learn: 0.5466247	total: 12.6ms	remaining: 2.42s
1:	learn: 0.5229454	total: 24.5ms	remaining: 2.34s
2:	learn: 0.5085832	total: 35.6ms	remaining: 2.25s
3:	learn: 0.5030283	total: 46.2ms	remaining: 2.18s
4:	learn: 0.4927559	total: 57.2ms	remaining: 2.15s
5:	learn: 0.4878708	total: 67.7ms	remaining: 2.11s
6:	learn: 0.4680490	total: 78.8ms	remaining: 2.1s
7:	learn: 0.4563400	total: 89.7ms	remaining: 2.07s
8:	learn: 0.4491985	total: 100ms	remaining: 2.05s
9:	learn: 0.4433819	total: 111ms	remaining: 2.02s
10:	learn: 0.4406326	total: 121ms	remaining: 2s
11:	learn: 0.4328116	total: 131ms	remaining: 1.98s
12:	learn: 0.4273933	total: 141ms	remaining: 1.96s
13:	learn: 0.4212282	total: 152ms	remaining: 1.94s
14:	learn: 0.4122540	total: 162ms	remaining: 1.93s
15:	learn: 0.4069292	total: 172ms	remaining: 1.9s
16:	learn: 0.4002548	total: 183ms	remaining: 1.89s
17:	learn: 0.3967281	total: 194ms	remaining: 1.88s
18:	learn: 0.3928288	total: 204ms	remaining: 1.87s
19:	learn: 0.3874009	total: 216ms	rema

166:	learn: 0.2598449	total: 1.76s	remaining: 273ms
167:	learn: 0.2595068	total: 1.77s	remaining: 263ms
168:	learn: 0.2592352	total: 1.78s	remaining: 252ms
169:	learn: 0.2589753	total: 1.79s	remaining: 242ms
170:	learn: 0.2587273	total: 1.8s	remaining: 231ms
171:	learn: 0.2585677	total: 1.81s	remaining: 221ms
172:	learn: 0.2584608	total: 1.82s	remaining: 210ms
173:	learn: 0.2580250	total: 1.83s	remaining: 200ms
174:	learn: 0.2577411	total: 1.84s	remaining: 189ms
175:	learn: 0.2575034	total: 1.85s	remaining: 179ms
176:	learn: 0.2572551	total: 1.86s	remaining: 168ms
177:	learn: 0.2570437	total: 1.87s	remaining: 158ms
178:	learn: 0.2567270	total: 1.88s	remaining: 147ms
179:	learn: 0.2564534	total: 1.89s	remaining: 137ms
180:	learn: 0.2563090	total: 1.9s	remaining: 126ms
181:	learn: 0.2559733	total: 1.91s	remaining: 116ms
182:	learn: 0.2557608	total: 1.93s	remaining: 105ms
183:	learn: 0.2554228	total: 1.94s	remaining: 94.7ms
184:	learn: 0.2551586	total: 1.95s	remaining: 84.2ms
185:	learn: 

In [50]:
for model in pipe_all:
    
    model_scores['Model Name'].append(str(model[0]).split('(')[0] + " SMOTE")
    
    model_scores['Accuracy train'].append(model.score(X_train_sm, y_train_sm))
    pred_tr = model.predict(X_train_sm)
    prob_tr = model.predict_proba(X_train_sm)[:,1]
    model_scores['Precision train'].append(precision_score(y_train_sm, pred_tr))
    model_scores['Recall train'].append(recall_score(y_train_sm, pred_tr))
    model_scores['F1 train'].append(f1_score(y_train_sm, pred_tr))
    model_scores['F1 Avg Weighted train'].append(f1_score(y_train_sm, pred_tr, average = 'weighted'))
    model_scores['F2 train'].append(fbeta_score(y_train_sm, pred_tr, beta = 2.0))
    model_scores['ROC AUC train'].append(roc_auc_score(y_train_sm, prob_tr))
    
    model_scores['Accuracy test'].append(model.score(X_test, y_test))
    pred_ts = model.predict(X_test)
    prob_ts = model.predict_proba(X_test)[:,1]
    model_scores['Precision test'].append(precision_score(y_test, pred_ts))
    model_scores['Recall test'].append(recall_score(y_test, pred_ts))
    model_scores['F1 test'].append(f1_score(y_test, pred_ts))
    model_scores['F1 Avg Weighted test'].append(f1_score(y_test, pred_ts, average = 'weighted'))
    model_scores['F2 test'].append(fbeta_score(y_test, pred_ts, beta = 2.0))
    model_scores['ROC AUC test'].append(roc_auc_score(y_test, prob_ts))

    model_scores['CV-5-Mean'].append(cross_val_score(model,X_train_sm,y_train_sm,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring=my_f2_scorer()).mean())
    model_scores['CV-5-SD'].append(cross_val_score(model,X_train_sm,y_train_sm,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring=my_f2_scorer()).std())

0:	learn: 0.5452743	total: 40.8ms	remaining: 7.83s
1:	learn: 0.5150047	total: 52.1ms	remaining: 4.97s
2:	learn: 0.4973337	total: 62.4ms	remaining: 3.95s
3:	learn: 0.4877834	total: 72ms	remaining: 3.4s
4:	learn: 0.4768797	total: 81.7ms	remaining: 3.07s
5:	learn: 0.4724530	total: 91.1ms	remaining: 2.84s
6:	learn: 0.4673211	total: 100ms	remaining: 2.67s
7:	learn: 0.4614571	total: 110ms	remaining: 2.55s
8:	learn: 0.4550911	total: 116ms	remaining: 2.36s
9:	learn: 0.4508920	total: 125ms	remaining: 2.29s
10:	learn: 0.4479765	total: 135ms	remaining: 2.23s
11:	learn: 0.4425778	total: 144ms	remaining: 2.18s
12:	learn: 0.4388235	total: 154ms	remaining: 2.14s
13:	learn: 0.4351003	total: 164ms	remaining: 2.09s
14:	learn: 0.4278866	total: 173ms	remaining: 2.05s
15:	learn: 0.4223966	total: 182ms	remaining: 2.02s
16:	learn: 0.4127821	total: 192ms	remaining: 1.99s
17:	learn: 0.4089607	total: 201ms	remaining: 1.96s
18:	learn: 0.4009844	total: 211ms	remaining: 1.93s
19:	learn: 0.3957602	total: 220ms	rema

164:	learn: 0.2561542	total: 1.61s	remaining: 273ms
165:	learn: 0.2559494	total: 1.62s	remaining: 263ms
166:	learn: 0.2558648	total: 1.63s	remaining: 253ms
167:	learn: 0.2554572	total: 1.64s	remaining: 244ms
168:	learn: 0.2551650	total: 1.65s	remaining: 234ms
169:	learn: 0.2549151	total: 1.66s	remaining: 224ms
170:	learn: 0.2547337	total: 1.67s	remaining: 214ms
171:	learn: 0.2545641	total: 1.67s	remaining: 204ms
172:	learn: 0.2542732	total: 1.68s	remaining: 195ms
173:	learn: 0.2539908	total: 1.69s	remaining: 185ms
174:	learn: 0.2537498	total: 1.7s	remaining: 175ms
175:	learn: 0.2534750	total: 1.71s	remaining: 165ms
176:	learn: 0.2533250	total: 1.72s	remaining: 156ms
177:	learn: 0.2531530	total: 1.73s	remaining: 146ms
178:	learn: 0.2529360	total: 1.74s	remaining: 136ms
179:	learn: 0.2526162	total: 1.75s	remaining: 126ms
180:	learn: 0.2523967	total: 1.76s	remaining: 117ms
181:	learn: 0.2522082	total: 1.77s	remaining: 107ms
182:	learn: 0.2518851	total: 1.78s	remaining: 97.2ms
183:	learn: 

142:	learn: 0.2643411	total: 1.38s	remaining: 483ms
143:	learn: 0.2640189	total: 1.39s	remaining: 474ms
144:	learn: 0.2637566	total: 1.4s	remaining: 464ms
145:	learn: 0.2635305	total: 1.41s	remaining: 454ms
146:	learn: 0.2633633	total: 1.42s	remaining: 444ms
147:	learn: 0.2629136	total: 1.43s	remaining: 435ms
148:	learn: 0.2624601	total: 1.44s	remaining: 425ms
149:	learn: 0.2621537	total: 1.45s	remaining: 415ms
150:	learn: 0.2619189	total: 1.46s	remaining: 406ms
151:	learn: 0.2617220	total: 1.47s	remaining: 396ms
152:	learn: 0.2614309	total: 1.48s	remaining: 386ms
153:	learn: 0.2611234	total: 1.49s	remaining: 376ms
154:	learn: 0.2609211	total: 1.49s	remaining: 367ms
155:	learn: 0.2605550	total: 1.5s	remaining: 357ms
156:	learn: 0.2603767	total: 1.51s	remaining: 347ms
157:	learn: 0.2600205	total: 1.52s	remaining: 337ms
158:	learn: 0.2597729	total: 1.53s	remaining: 328ms
159:	learn: 0.2595241	total: 1.54s	remaining: 318ms
160:	learn: 0.2592685	total: 1.55s	remaining: 308ms
161:	learn: 0.

121:	learn: 0.2719586	total: 1.18s	remaining: 686ms
122:	learn: 0.2716377	total: 1.19s	remaining: 677ms
123:	learn: 0.2714140	total: 1.2s	remaining: 666ms
124:	learn: 0.2711317	total: 1.21s	remaining: 656ms
125:	learn: 0.2707680	total: 1.22s	remaining: 647ms
126:	learn: 0.2704657	total: 1.23s	remaining: 637ms
127:	learn: 0.2702043	total: 1.24s	remaining: 627ms
128:	learn: 0.2698818	total: 1.24s	remaining: 618ms
129:	learn: 0.2695119	total: 1.25s	remaining: 608ms
130:	learn: 0.2691597	total: 1.26s	remaining: 598ms
131:	learn: 0.2688040	total: 1.27s	remaining: 588ms
132:	learn: 0.2685332	total: 1.28s	remaining: 578ms
133:	learn: 0.2683251	total: 1.29s	remaining: 568ms
134:	learn: 0.2680838	total: 1.3s	remaining: 559ms
135:	learn: 0.2676734	total: 1.31s	remaining: 549ms
136:	learn: 0.2672460	total: 1.32s	remaining: 539ms
137:	learn: 0.2667849	total: 1.33s	remaining: 530ms
138:	learn: 0.2664642	total: 1.34s	remaining: 520ms
139:	learn: 0.2662119	total: 1.35s	remaining: 510ms
140:	learn: 0.

101:	learn: 0.2798086	total: 988ms	remaining: 882ms
102:	learn: 0.2794833	total: 998ms	remaining: 872ms
103:	learn: 0.2792468	total: 1.01s	remaining: 862ms
104:	learn: 0.2787556	total: 1.02s	remaining: 852ms
105:	learn: 0.2784127	total: 1.02s	remaining: 842ms
106:	learn: 0.2779806	total: 1.04s	remaining: 833ms
107:	learn: 0.2776171	total: 1.04s	remaining: 823ms
108:	learn: 0.2770583	total: 1.05s	remaining: 814ms
109:	learn: 0.2765743	total: 1.06s	remaining: 804ms
110:	learn: 0.2760620	total: 1.07s	remaining: 794ms
111:	learn: 0.2757308	total: 1.08s	remaining: 785ms
112:	learn: 0.2752050	total: 1.09s	remaining: 775ms
113:	learn: 0.2745931	total: 1.1s	remaining: 765ms
114:	learn: 0.2742120	total: 1.11s	remaining: 755ms
115:	learn: 0.2737942	total: 1.12s	remaining: 745ms
116:	learn: 0.2733342	total: 1.13s	remaining: 736ms
117:	learn: 0.2728149	total: 1.14s	remaining: 726ms
118:	learn: 0.2724364	total: 1.15s	remaining: 716ms
119:	learn: 0.2721754	total: 1.16s	remaining: 706ms
120:	learn: 0

...

38:	learn: 0.3386638	total: 384ms	remaining: 1.52s
39:	learn: 0.3344096	total: 394ms	remaining: 1.51s
40:	learn: 0.3313178	total: 404ms	remaining: 1.5s
41:	learn: 0.3281129	total: 414ms	remaining: 1.49s
42:	learn: 0.3270218	total: 423ms	remaining: 1.48s
43:	learn: 0.3249330	total: 433ms	remaining: 1.46s
44:	learn: 0.3230234	total: 441ms	remaining: 1.45s
45:	learn: 0.3222113	total: 451ms	remaining: 1.44s
46:	learn: 0.3212312	total: 460ms	remaining: 1.43s
47:	learn: 0.3200438	total: 470ms	remaining: 1.42s
48:	learn: 0.3173666	total: 479ms	remaining: 1.41s
49:	learn: 0.3139013	total: 488ms	remaining: 1.4s
50:	learn: 0.3114188	total: 498ms	remaining: 1.39s
51:	learn: 0.3100759	total: 508ms	remaining: 1.38s
52:	learn: 0.3091226	total: 518ms	remaining: 1.37s
53:	learn: 0.3084272	total: 527ms	remaining: 1.36s
54:	learn: 0.3077633	total: 537ms	remaining: 1.35s
55:	learn: 0.3071147	total: 546ms	remaining: 1.33s
56:	learn: 0.3036482	total: 556ms	remaining: 1.33s
57:	learn: 0.3016693	total: 566ms

20:	learn: 0.3893635	total: 210ms	remaining: 1.72s
21:	learn: 0.3857424	total: 220ms	remaining: 1.71s
22:	learn: 0.3819202	total: 229ms	remaining: 1.69s
23:	learn: 0.3783143	total: 238ms	remaining: 1.68s
24:	learn: 0.3764936	total: 248ms	remaining: 1.67s
25:	learn: 0.3740556	total: 258ms	remaining: 1.66s
26:	learn: 0.3707768	total: 267ms	remaining: 1.64s
27:	learn: 0.3656005	total: 277ms	remaining: 1.63s
28:	learn: 0.3640434	total: 286ms	remaining: 1.62s
29:	learn: 0.3626442	total: 295ms	remaining: 1.6s
30:	learn: 0.3611632	total: 304ms	remaining: 1.59s
31:	learn: 0.3577407	total: 315ms	remaining: 1.58s
32:	learn: 0.3539720	total: 324ms	remaining: 1.57s
33:	learn: 0.3520103	total: 333ms	remaining: 1.56s
34:	learn: 0.3505192	total: 343ms	remaining: 1.55s
35:	learn: 0.3493658	total: 353ms	remaining: 1.54s
36:	learn: 0.3463122	total: 362ms	remaining: 1.53s
37:	learn: 0.3451290	total: 372ms	remaining: 1.51s
38:	learn: 0.3410762	total: 381ms	remaining: 1.5s
39:	learn: 0.3381226	total: 391ms

0:	learn: 0.5476493	total: 13.1ms	remaining: 2.52s
1:	learn: 0.5184446	total: 24ms	remaining: 2.29s
2:	learn: 0.4976440	total: 34.7ms	remaining: 2.2s
3:	learn: 0.4887138	total: 44.4ms	remaining: 2.1s
4:	learn: 0.4821441	total: 54.4ms	remaining: 2.05s
5:	learn: 0.4776997	total: 64.2ms	remaining: 2s
6:	learn: 0.4669796	total: 74.4ms	remaining: 1.98s
7:	learn: 0.4584092	total: 84.5ms	remaining: 1.95s
8:	learn: 0.4545807	total: 90.1ms	remaining: 1.84s
9:	learn: 0.4512481	total: 99.5ms	remaining: 1.82s
10:	learn: 0.4424601	total: 109ms	remaining: 1.81s
11:	learn: 0.4385261	total: 118ms	remaining: 1.78s
12:	learn: 0.4322884	total: 127ms	remaining: 1.76s
13:	learn: 0.4278142	total: 137ms	remaining: 1.76s
14:	learn: 0.4203298	total: 147ms	remaining: 1.74s
15:	learn: 0.4178365	total: 156ms	remaining: 1.73s
16:	learn: 0.4110398	total: 166ms	remaining: 1.72s
17:	learn: 0.4067576	total: 176ms	remaining: 1.71s
18:	learn: 0.4042267	total: 185ms	remaining: 1.69s
19:	learn: 0.3978044	total: 194ms	rema

162:	learn: 0.2589028	total: 1.55s	remaining: 286ms
163:	learn: 0.2586970	total: 1.56s	remaining: 277ms
164:	learn: 0.2584610	total: 1.57s	remaining: 267ms
165:	learn: 0.2582350	total: 1.58s	remaining: 258ms
166:	learn: 0.2579586	total: 1.59s	remaining: 248ms
167:	learn: 0.2578475	total: 1.6s	remaining: 238ms
168:	learn: 0.2575134	total: 1.61s	remaining: 229ms
169:	learn: 0.2572053	total: 1.62s	remaining: 219ms
170:	learn: 0.2569152	total: 1.63s	remaining: 210ms
171:	learn: 0.2566120	total: 1.64s	remaining: 200ms
172:	learn: 0.2564075	total: 1.65s	remaining: 191ms
173:	learn: 0.2561514	total: 1.66s	remaining: 181ms
174:	learn: 0.2558927	total: 1.67s	remaining: 172ms
175:	learn: 0.2556726	total: 1.68s	remaining: 162ms
176:	learn: 0.2554803	total: 1.69s	remaining: 152ms
177:	learn: 0.2551445	total: 1.7s	remaining: 143ms
178:	learn: 0.2549031	total: 1.71s	remaining: 133ms
179:	learn: 0.2545496	total: 1.72s	remaining: 124ms
180:	learn: 0.2542183	total: 1.72s	remaining: 114ms
181:	learn: 0.

147:	learn: 0.2639501	total: 1.41s	remaining: 429ms
148:	learn: 0.2634510	total: 1.42s	remaining: 420ms
149:	learn: 0.2631640	total: 1.43s	remaining: 410ms
150:	learn: 0.2629769	total: 1.44s	remaining: 400ms
151:	learn: 0.2626338	total: 1.45s	remaining: 391ms
152:	learn: 0.2624434	total: 1.46s	remaining: 381ms
153:	learn: 0.2623103	total: 1.47s	remaining: 372ms
154:	learn: 0.2619401	total: 1.48s	remaining: 362ms
155:	learn: 0.2616647	total: 1.49s	remaining: 353ms
156:	learn: 0.2614491	total: 1.5s	remaining: 343ms
157:	learn: 0.2610561	total: 1.5s	remaining: 334ms
158:	learn: 0.2605979	total: 1.51s	remaining: 324ms
159:	learn: 0.2603330	total: 1.52s	remaining: 315ms
160:	learn: 0.2598107	total: 1.53s	remaining: 305ms
161:	learn: 0.2594175	total: 1.54s	remaining: 296ms
162:	learn: 0.2591887	total: 1.55s	remaining: 286ms
163:	learn: 0.2589139	total: 1.56s	remaining: 277ms
164:	learn: 0.2587223	total: 1.57s	remaining: 267ms
165:	learn: 0.2584715	total: 1.58s	remaining: 257ms
166:	learn: 0.

In [51]:
pd.DataFrame(model_scores).round(4)

Model Name  Accuracy train  \
0                                  LogisticRegression        0.819900   
1                              DecisionTreeClassifier        0.811700   
2                              RandomForestClassifier        0.825000   
3                                          GaussianNB        0.791100   
4                                         BernoulliNB        0.819500   
5                                  AdaBoostClassifier        0.201900   
6                          GradientBoostingClassifier        0.276200   
7                                       XGBClassifier        0.754400   
8   <catboost.core.CatBoostClassifier object at 0x...        0.859400   
9                                      LGBMClassifier        0.574300   
10                               KNeighborsClassifier        0.850200   
11                           LogisticRegression SMOTE        0.674800   
12                       DecisionTreeClassifier SMOTE        0.621900   
13                       RandomForestClassifier SMOTE        0.682200   
14                                   GaussianNB SMOTE        0.649400   
15                                  BernoulliNB SMOTE        0.666600   
16                           AdaBoostClassifier SMOTE        0.325500   
17                   GradientBoostingClassifier SMOTE        0.519200   
18                                XGBClassifier SMOTE        0.678900   
19  <catboost.core.CatBoostClassifier object at 0x...        0.896400   
20                               LGBMClassifier SMOTE        0.446600   
21                         KNeighborsClassifier SMOTE        0.846600   

    Precision train  Recall train  F1 train  F1 Avg Weighted train  F2 train  \
0          0.758000      0.158800  0.262600               0.769200  0.188600   
1          0.564400      0.296500  0.388800               0.787800  0.327600   
2          0.691800      0.240800  0.357200               0.789400  0.276900   
3          0.472400      0.292600  0.361400               0.771400  0.316700   
4          0.685800      0.195700  0.304600               0.776800  0.228400   
5          0.201900      1.000000  0.336000               0.067900  0.558500   
6          0.203400      0.886300  0.330900               0.235800  0.530300   
7          0.398900      0.426000  0.412000               0.757400  0.420300   
8          0.839100      0.375500  0.518900               0.837100  0.422200   
9          0.290000      0.764900  0.420500               0.614500  0.576200   
10         0.737300      0.401400  0.519800               0.832200  0.441600   
11         0.703300      0.604800  0.650300               0.673200  0.622200   
12         0.839000      0.301800  0.443900               0.578800  0.346100   
13         0.624700      0.912300  0.741600               0.664400  0.835400   
14         0.641200      0.678500  0.659300               0.649100  0.670700   
15         0.683900      0.619400  0.650100               0.665800  0.631300   
16         0.214900      0.131500  0.163200               0.299100  0.142600   
17         0.510800      0.905500  0.653200               0.434800  0.784300   
18         0.624400      0.898200  0.736700               0.662700  0.825800   
19         0.960900      0.826500  0.888600               0.895900  0.850300   
20         0.441600      0.403200  0.421500               0.445600  0.410300   
21         0.823100      0.883000  0.852000               0.846400  0.870300   

    ROC AUC train  Accuracy test  Precision test  Recall test  F1 test  \
0        0.740900       0.818300        0.750200     0.150200 0.250300   
1        0.643600       0.809200        0.553400     0.285400 0.376600   
2        0.746500       0.823100        0.682300     0.231900 0.346200   
3        0.697800       0.789500        0.465800     0.289300 0.356900   
4        0.713700       0.817200        0.671900     0.185600 0.290900   
5        0.619300       0.201900        0.201900     1.000000 0.336000   
6   

In [52]:
from imblearn.over_sampling import ADASYN
from collections import Counter

counter = Counter(y_train)
print('Before', counter)

ada = ADASYN(random_state=10)
X_train_as, y_train_as = ada.fit_resample(X_train, y_train)

counter = Counter(y_train_as)
print('After', counter)

Before Counter({0: 61743, 1: 15623})
After Counter({1: 64826, 0: 61743})


In [53]:
lr_pipeline = Pipeline([
    ('lr_model', LogisticRegression(**rsearch_lr.best_params_))
])

In [54]:
dt_pipeline = Pipeline([
    ('dt_model', DecisionTreeClassifier(**rsearch_dt.best_params_,random_state=42))
])

In [55]:
rf_pipeline = Pipeline([
    ('rf_model', RandomForestClassifier(**rsearch_rf.best_params_,random_state=42))
])

In [56]:
gnb_pipeline = Pipeline([
    ('gnb_model', GaussianNB())
])

In [57]:
bnb_pipeline = Pipeline([
    ('bnb_model', BernoulliNB())
])

In [58]:
knn_pipeline = Pipeline([
    ('knn_model', KNeighborsClassifier())
])

In [59]:
ada_pipeline = Pipeline([
    ('ada_model', AdaBoostClassifier(**rsearch_ada.best_params_, random_state = 42))
])

In [60]:
gb_pipeline = Pipeline([
    ('gb_model', GradientBoostingClassifier(**rsearch_gb.best_params_, random_state = 42))
])

In [61]:
cb_pipeline = Pipeline([
    ('cb_model', CatBoostClassifier(**rsearch_cb.best_params_, random_state = 42))
])

In [62]:
lgbm_pipeline = Pipeline([
    ('lgbm_model', LGBMClassifier(**rsearch_lgbm.best_params_, random_state = 42))
])

In [63]:
xgb_pipeline = Pipeline([
    ('xgb_model', XGBClassifier(**rsearch_xgb.best_params_, random_state = 42))
])

In [64]:
pipe_all = [lr_pipeline, dt_pipeline, rf_pipeline, gnb_pipeline, bnb_pipeline, ada_pipeline, gb_pipeline, xgb_pipeline, cb_pipeline, lgbm_pipeline,
            knn_pipeline]
            
for pipe in pipe_all:
  pipe.fit(X_train_as, y_train_as)

0:	learn: 0.5608540	total: 37ms	remaining: 7.11s
1:	learn: 0.5343933	total: 48.9ms	remaining: 4.67s
2:	learn: 0.5233572	total: 59.4ms	remaining: 3.76s
3:	learn: 0.5177639	total: 70.1ms	remaining: 3.31s
4:	learn: 0.4891660	total: 82.9ms	remaining: 3.12s
5:	learn: 0.4782821	total: 95.2ms	remaining: 2.97s
6:	learn: 0.4702560	total: 106ms	remaining: 2.82s
7:	learn: 0.4656322	total: 117ms	remaining: 2.71s
8:	learn: 0.4554241	total: 129ms	remaining: 2.63s
9:	learn: 0.4511297	total: 139ms	remaining: 2.54s
10:	learn: 0.4466425	total: 150ms	remaining: 2.48s
11:	learn: 0.4402738	total: 160ms	remaining: 2.41s
12:	learn: 0.4381892	total: 170ms	remaining: 2.35s
13:	learn: 0.4334014	total: 181ms	remaining: 2.31s
14:	learn: 0.4279386	total: 191ms	remaining: 2.27s
15:	learn: 0.4194710	total: 202ms	remaining: 2.23s
16:	learn: 0.4120906	total: 213ms	remaining: 2.2s
17:	learn: 0.4050620	total: 224ms	remaining: 2.17s
18:	learn: 0.3973667	total: 234ms	remaining: 2.15s
19:	learn: 0.3924778	total: 244ms	rema

161:	learn: 0.2582808	total: 1.76s	remaining: 336ms
162:	learn: 0.2580593	total: 1.77s	remaining: 326ms
163:	learn: 0.2579365	total: 1.78s	remaining: 315ms
164:	learn: 0.2575315	total: 1.79s	remaining: 304ms
165:	learn: 0.2573038	total: 1.8s	remaining: 293ms
166:	learn: 0.2571915	total: 1.81s	remaining: 282ms
167:	learn: 0.2570403	total: 1.82s	remaining: 271ms
168:	learn: 0.2567739	total: 1.83s	remaining: 260ms
169:	learn: 0.2565598	total: 1.84s	remaining: 249ms
170:	learn: 0.2562765	total: 1.85s	remaining: 238ms
171:	learn: 0.2561249	total: 1.86s	remaining: 227ms
172:	learn: 0.2559547	total: 1.87s	remaining: 217ms
173:	learn: 0.2556261	total: 1.88s	remaining: 206ms
174:	learn: 0.2552157	total: 1.89s	remaining: 195ms
175:	learn: 0.2550167	total: 1.91s	remaining: 184ms
176:	learn: 0.2548655	total: 1.92s	remaining: 173ms
177:	learn: 0.2545733	total: 1.93s	remaining: 162ms
178:	learn: 0.2540440	total: 1.94s	remaining: 152ms
179:	learn: 0.2538742	total: 1.95s	remaining: 141ms
180:	learn: 0

In [65]:
for model in pipe_all:
    
    model_scores['Model Name'].append(str(model[0]).split('(')[0] + " ADASYN")
    
    model_scores['Accuracy train'].append(model.score(X_train_as, y_train_as))
    pred_tr = model.predict(X_train_as)
    prob_tr = model.predict_proba(X_train_as)[:,1]
    model_scores['Precision train'].append(precision_score(y_train_as, pred_tr))
    model_scores['Recall train'].append(recall_score(y_train_as, pred_tr))
    model_scores['F1 train'].append(f1_score(y_train_as, pred_tr))
    model_scores['F1 Avg Weighted train'].append(f1_score(y_train_as, pred_tr, average = 'weighted'))
    model_scores['F2 train'].append(fbeta_score(y_train_as, pred_tr, beta = 2.0))
    model_scores['ROC AUC train'].append(roc_auc_score(y_train_as, prob_tr))
    
    model_scores['Accuracy test'].append(model.score(X_test, y_test))
    pred_ts = model.predict(X_test)
    prob_ts = model.predict_proba(X_test)[:,1]
    model_scores['Precision test'].append(precision_score(y_test, pred_ts))
    model_scores['Recall test'].append(recall_score(y_test, pred_ts))
    model_scores['F1 test'].append(f1_score(y_test, pred_ts))
    model_scores['F1 Avg Weighted test'].append(f1_score(y_test, pred_ts, average = 'weighted'))
    model_scores['F2 test'].append(fbeta_score(y_test, pred_ts, beta = 2.0))
    model_scores['ROC AUC test'].append(roc_auc_score(y_test, prob_ts))

    model_scores['CV-5-Mean'].append(cross_val_score(model,X_train_as,y_train_as,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring=my_f2_scorer()).mean())
    model_scores['CV-5-SD'].append(cross_val_score(model,X_train_as,y_train_as,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring=my_f2_scorer()).std())

0:	learn: 0.5643131	total: 20ms	remaining: 3.83s
1:	learn: 0.5488534	total: 31.2ms	remaining: 2.98s
2:	learn: 0.5398169	total: 41.5ms	remaining: 2.63s
3:	learn: 0.5276625	total: 52.8ms	remaining: 2.5s
4:	learn: 0.5216390	total: 63.2ms	remaining: 2.38s
5:	learn: 0.4946265	total: 74.6ms	remaining: 2.32s
6:	learn: 0.4905315	total: 84.8ms	remaining: 2.25s
7:	learn: 0.4813424	total: 95.3ms	remaining: 2.2s
8:	learn: 0.4775111	total: 105ms	remaining: 2.15s
9:	learn: 0.4705235	total: 115ms	remaining: 2.11s
10:	learn: 0.4551418	total: 125ms	remaining: 2.07s
11:	learn: 0.4422404	total: 135ms	remaining: 2.04s
12:	learn: 0.4349844	total: 145ms	remaining: 2.01s
13:	learn: 0.4304292	total: 155ms	remaining: 1.98s
14:	learn: 0.4225596	total: 165ms	remaining: 1.95s
15:	learn: 0.4175111	total: 175ms	remaining: 1.93s
16:	learn: 0.4147609	total: 184ms	remaining: 1.91s
17:	learn: 0.4124082	total: 194ms	remaining: 1.88s
18:	learn: 0.4061347	total: 204ms	remaining: 1.87s
19:	learn: 0.4007475	total: 213ms	rem

175:	learn: 0.2515856	total: 1.75s	remaining: 169ms
176:	learn: 0.2513628	total: 1.76s	remaining: 159ms
177:	learn: 0.2510732	total: 1.77s	remaining: 149ms
178:	learn: 0.2507900	total: 1.78s	remaining: 139ms
179:	learn: 0.2505814	total: 1.79s	remaining: 129ms
180:	learn: 0.2504437	total: 1.8s	remaining: 119ms
181:	learn: 0.2501879	total: 1.81s	remaining: 109ms
182:	learn: 0.2500415	total: 1.82s	remaining: 99.4ms
183:	learn: 0.2498489	total: 1.83s	remaining: 89.5ms
184:	learn: 0.2494217	total: 1.84s	remaining: 79.5ms
185:	learn: 0.2492146	total: 1.85s	remaining: 69.6ms
186:	learn: 0.2489042	total: 1.86s	remaining: 59.6ms
187:	learn: 0.2486263	total: 1.87s	remaining: 49.7ms
188:	learn: 0.2483256	total: 1.88s	remaining: 39.7ms
189:	learn: 0.2481162	total: 1.89s	remaining: 29.8ms
190:	learn: 0.2479818	total: 1.9s	remaining: 19.8ms
191:	learn: 0.2478477	total: 1.91s	remaining: 9.92ms
192:	learn: 0.2475056	total: 1.91s	remaining: 0us
0:	learn: 0.5646209	total: 30.8ms	remaining: 5.91s
1:	lear

158:	learn: 0.2572323	total: 1.56s	remaining: 335ms
159:	learn: 0.2569568	total: 1.57s	remaining: 325ms
160:	learn: 0.2567964	total: 1.58s	remaining: 315ms
161:	learn: 0.2565197	total: 1.59s	remaining: 305ms
162:	learn: 0.2562603	total: 1.6s	remaining: 295ms
163:	learn: 0.2560232	total: 1.61s	remaining: 285ms
164:	learn: 0.2558978	total: 1.62s	remaining: 275ms
165:	learn: 0.2556985	total: 1.63s	remaining: 265ms
166:	learn: 0.2555303	total: 1.64s	remaining: 256ms
167:	learn: 0.2551621	total: 1.65s	remaining: 246ms
168:	learn: 0.2549204	total: 1.66s	remaining: 236ms
169:	learn: 0.2544377	total: 1.67s	remaining: 226ms
170:	learn: 0.2542019	total: 1.68s	remaining: 216ms
171:	learn: 0.2538917	total: 1.69s	remaining: 206ms
172:	learn: 0.2537638	total: 1.7s	remaining: 196ms
173:	learn: 0.2535631	total: 1.71s	remaining: 187ms
174:	learn: 0.2533419	total: 1.72s	remaining: 177ms
175:	learn: 0.2531470	total: 1.73s	remaining: 167ms
176:	learn: 0.2528889	total: 1.74s	remaining: 157ms
177:	learn: 0.

136:	learn: 0.2631705	total: 1.33s	remaining: 544ms
137:	learn: 0.2628428	total: 1.34s	remaining: 534ms
138:	learn: 0.2625954	total: 1.35s	remaining: 525ms
139:	learn: 0.2624071	total: 1.36s	remaining: 515ms
140:	learn: 0.2620701	total: 1.37s	remaining: 506ms
141:	learn: 0.2617034	total: 1.38s	remaining: 496ms
142:	learn: 0.2614364	total: 1.39s	remaining: 486ms
143:	learn: 0.2611237	total: 1.4s	remaining: 477ms
144:	learn: 0.2608695	total: 1.41s	remaining: 467ms
145:	learn: 0.2607368	total: 1.42s	remaining: 458ms
146:	learn: 0.2604897	total: 1.43s	remaining: 448ms
147:	learn: 0.2601637	total: 1.44s	remaining: 439ms
148:	learn: 0.2596522	total: 1.45s	remaining: 430ms
149:	learn: 0.2592955	total: 1.46s	remaining: 420ms
150:	learn: 0.2589208	total: 1.48s	remaining: 410ms
151:	learn: 0.2585456	total: 1.49s	remaining: 401ms
152:	learn: 0.2582037	total: 1.5s	remaining: 391ms
153:	learn: 0.2580077	total: 1.5s	remaining: 381ms
154:	learn: 0.2578114	total: 1.52s	remaining: 372ms
155:	learn: 0.2

116:	learn: 0.2703270	total: 1.14s	remaining: 740ms
117:	learn: 0.2699439	total: 1.15s	remaining: 731ms
118:	learn: 0.2697757	total: 1.16s	remaining: 721ms
119:	learn: 0.2693945	total: 1.17s	remaining: 711ms
120:	learn: 0.2691154	total: 1.18s	remaining: 701ms
121:	learn: 0.2686107	total: 1.19s	remaining: 691ms
122:	learn: 0.2683481	total: 1.2s	remaining: 681ms
123:	learn: 0.2680951	total: 1.21s	remaining: 672ms
124:	learn: 0.2680351	total: 1.22s	remaining: 661ms
125:	learn: 0.2677530	total: 1.23s	remaining: 651ms
126:	learn: 0.2675282	total: 1.23s	remaining: 641ms
127:	learn: 0.2670525	total: 1.24s	remaining: 632ms
128:	learn: 0.2667605	total: 1.25s	remaining: 622ms
129:	learn: 0.2663323	total: 1.26s	remaining: 612ms
130:	learn: 0.2658893	total: 1.27s	remaining: 602ms
131:	learn: 0.2656466	total: 1.28s	remaining: 593ms
132:	learn: 0.2651861	total: 1.29s	remaining: 583ms
133:	learn: 0.2648977	total: 1.3s	remaining: 573ms
134:	learn: 0.2646147	total: 1.31s	remaining: 563ms
135:	learn: 0.

...

59:	learn: 0.2973860	total: 609ms	remaining: 1.35s
60:	learn: 0.2969875	total: 619ms	remaining: 1.34s
61:	learn: 0.2963530	total: 629ms	remaining: 1.33s
62:	learn: 0.2956260	total: 638ms	remaining: 1.32s
63:	learn: 0.2950636	total: 647ms	remaining: 1.3s
64:	learn: 0.2943741	total: 657ms	remaining: 1.29s
65:	learn: 0.2935456	total: 666ms	remaining: 1.28s
66:	learn: 0.2931701	total: 676ms	remaining: 1.27s
67:	learn: 0.2926422	total: 685ms	remaining: 1.26s
68:	learn: 0.2921034	total: 695ms	remaining: 1.25s
69:	learn: 0.2915816	total: 704ms	remaining: 1.24s
70:	learn: 0.2907529	total: 714ms	remaining: 1.23s
71:	learn: 0.2899709	total: 724ms	remaining: 1.22s
72:	learn: 0.2896444	total: 734ms	remaining: 1.21s
73:	learn: 0.2892635	total: 743ms	remaining: 1.19s
74:	learn: 0.2886526	total: 752ms	remaining: 1.18s
75:	learn: 0.2881146	total: 762ms	remaining: 1.17s
76:	learn: 0.2875574	total: 771ms	remaining: 1.16s
77:	learn: 0.2869412	total: 781ms	remaining: 1.15s
78:	learn: 0.2864929	total: 790m

40:	learn: 0.3281346	total: 403ms	remaining: 1.5s
41:	learn: 0.3233939	total: 413ms	remaining: 1.49s
42:	learn: 0.3224601	total: 423ms	remaining: 1.47s
43:	learn: 0.3213189	total: 432ms	remaining: 1.46s
44:	learn: 0.3166000	total: 442ms	remaining: 1.45s
45:	learn: 0.3154026	total: 452ms	remaining: 1.44s
46:	learn: 0.3147896	total: 461ms	remaining: 1.43s
47:	learn: 0.3134109	total: 470ms	remaining: 1.42s
48:	learn: 0.3122128	total: 480ms	remaining: 1.41s
49:	learn: 0.3111123	total: 490ms	remaining: 1.4s
50:	learn: 0.3104108	total: 499ms	remaining: 1.39s
51:	learn: 0.3064004	total: 509ms	remaining: 1.38s
52:	learn: 0.3051004	total: 519ms	remaining: 1.37s
53:	learn: 0.3036807	total: 529ms	remaining: 1.36s
54:	learn: 0.3030085	total: 539ms	remaining: 1.35s
55:	learn: 0.3024472	total: 548ms	remaining: 1.34s
56:	learn: 0.2999663	total: 558ms	remaining: 1.33s
57:	learn: 0.2992935	total: 568ms	remaining: 1.32s
58:	learn: 0.2985332	total: 577ms	remaining: 1.31s
59:	learn: 0.2974805	total: 587ms

19:	learn: 0.3989983	total: 223ms	remaining: 1.93s
20:	learn: 0.3927875	total: 233ms	remaining: 1.91s
21:	learn: 0.3885004	total: 242ms	remaining: 1.88s
22:	learn: 0.3836773	total: 252ms	remaining: 1.86s
23:	learn: 0.3795901	total: 261ms	remaining: 1.84s
24:	learn: 0.3774435	total: 270ms	remaining: 1.82s
25:	learn: 0.3718098	total: 280ms	remaining: 1.8s
26:	learn: 0.3671809	total: 289ms	remaining: 1.78s
27:	learn: 0.3618697	total: 300ms	remaining: 1.77s
28:	learn: 0.3587719	total: 309ms	remaining: 1.75s
29:	learn: 0.3557710	total: 318ms	remaining: 1.73s
30:	learn: 0.3530628	total: 328ms	remaining: 1.71s
31:	learn: 0.3512792	total: 337ms	remaining: 1.69s
32:	learn: 0.3485493	total: 346ms	remaining: 1.68s
33:	learn: 0.3456624	total: 356ms	remaining: 1.66s
34:	learn: 0.3422669	total: 366ms	remaining: 1.65s
35:	learn: 0.3411027	total: 375ms	remaining: 1.64s
36:	learn: 0.3400981	total: 385ms	remaining: 1.62s
37:	learn: 0.3366805	total: 396ms	remaining: 1.62s
38:	learn: 0.3337607	total: 407m

181:	learn: 0.2513937	total: 1.79s	remaining: 108ms
182:	learn: 0.2511015	total: 1.8s	remaining: 98.3ms
183:	learn: 0.2509162	total: 1.81s	remaining: 88.4ms
184:	learn: 0.2506564	total: 1.82s	remaining: 78.6ms
185:	learn: 0.2502982	total: 1.83s	remaining: 68.7ms
186:	learn: 0.2501760	total: 1.83s	remaining: 58.9ms
187:	learn: 0.2499624	total: 1.84s	remaining: 49.1ms
188:	learn: 0.2498096	total: 1.85s	remaining: 39.2ms
189:	learn: 0.2495411	total: 1.86s	remaining: 29.4ms
190:	learn: 0.2492332	total: 1.87s	remaining: 19.6ms
191:	learn: 0.2490927	total: 1.88s	remaining: 9.81ms
192:	learn: 0.2488911	total: 1.89s	remaining: 0us
0:	learn: 0.5716220	total: 15ms	remaining: 2.88s
1:	learn: 0.5336741	total: 25.3ms	remaining: 2.41s
2:	learn: 0.5238113	total: 34.7ms	remaining: 2.2s
3:	learn: 0.5164774	total: 44.3ms	remaining: 2.09s
4:	learn: 0.4952966	total: 54.5ms	remaining: 2.05s
5:	learn: 0.4900615	total: 64.1ms	remaining: 2s
6:	learn: 0.4853325	total: 73.9ms	remaining: 1.96s
7:	learn: 0.481003

159:	learn: 0.2575393	total: 1.55s	remaining: 320ms
160:	learn: 0.2572477	total: 1.56s	remaining: 310ms
161:	learn: 0.2570037	total: 1.57s	remaining: 300ms
162:	learn: 0.2567627	total: 1.58s	remaining: 290ms
163:	learn: 0.2565187	total: 1.59s	remaining: 281ms
164:	learn: 0.2561845	total: 1.6s	remaining: 271ms
165:	learn: 0.2560328	total: 1.61s	remaining: 261ms
166:	learn: 0.2558749	total: 1.62s	remaining: 252ms
167:	learn: 0.2556711	total: 1.63s	remaining: 242ms
168:	learn: 0.2553675	total: 1.64s	remaining: 232ms
169:	learn: 0.2552081	total: 1.65s	remaining: 223ms
170:	learn: 0.2550334	total: 1.66s	remaining: 213ms
171:	learn: 0.2547097	total: 1.67s	remaining: 203ms
172:	learn: 0.2545435	total: 1.67s	remaining: 194ms
173:	learn: 0.2542887	total: 1.68s	remaining: 184ms
174:	learn: 0.2540183	total: 1.69s	remaining: 174ms
175:	learn: 0.2538051	total: 1.7s	remaining: 164ms
176:	learn: 0.2534631	total: 1.71s	remaining: 155ms
177:	learn: 0.2532108	total: 1.72s	remaining: 145ms
178:	learn: 0.

In [66]:
pd.DataFrame(model_scores).round(4)

Model Name  Accuracy train  \
0                                  LogisticRegression        0.819900   
1                              DecisionTreeClassifier        0.811700   
2                              RandomForestClassifier        0.825000   
3                                          GaussianNB        0.791100   
4                                         BernoulliNB        0.819500   
5                                  AdaBoostClassifier        0.201900   
6                          GradientBoostingClassifier        0.276200   
7                                       XGBClassifier        0.754400   
8   <catboost.core.CatBoostClassifier object at 0x...        0.859400   
9                                      LGBMClassifier        0.574300   
10                               KNeighborsClassifier        0.850200   
11                           LogisticRegression SMOTE        0.674800   
12                       DecisionTreeClassifier SMOTE        0.621900   
13                       RandomForestClassifier SMOTE        0.682200   
14                                   GaussianNB SMOTE        0.649400   
15                                  BernoulliNB SMOTE        0.666600   
16                           AdaBoostClassifier SMOTE        0.325500   
17                   GradientBoostingClassifier SMOTE        0.519200   
18                                XGBClassifier SMOTE        0.678900   
19  <catboost.core.CatBoostClassifier object at 0x...        0.896400   
20                               LGBMClassifier SMOTE        0.446600   
21                         KNeighborsClassifier SMOTE        0.846600   
22                          LogisticRegression ADASYN        0.646700   
23                      DecisionTreeClassifier ADASYN        0.568200   
24                      RandomForestClassifier ADASYN        0.681900   
25                                  GaussianNB ADASYN        0.580200   
26                                 BernoulliNB ADASYN        0.647000   
27                          AdaBoostClassifier ADASYN        0.322800   
28                  GradientBoostingClassifier ADASYN        0.642400   
29                               XGBClassifier ADASYN        0.592300   
30  <catboost.core.CatBoostClassifier object at 0x...        0.895900   
31                              LGBMClassifier ADASYN        0.512200   
32                        KNeighborsClassifier ADASYN        0.834400   

    Precision train  Recall train  F1 train  F1 Avg Weighted train  F2 train  \
0          0.758000      0.158800  0.262600               0.769200  0.188600   
1          0.564400      0.296500  0.388800               0.787800  0.327600   
2          0.691800      0.240800  0.357200               0.789400  0.276900   
3          0.472400      0.292600  0.361400               0.771400  0.316700   
4          0.685800      0.195700  0.304600               0.776800  0.228400   
5          0.201900      1.000000  0.336000               0.067900  0.558500   
6          0.203400      0.886300  0.330900               0.235800  0.530300   
7          0.398900      0.426000  0.412000               0.757400  0.420300   
8          0.839100      0.375500  0.518900               0.837100  0.422200   
9          0.290000      0.764900  0.420500               0.614500  0.576200   
10         0.737300      0.401400  0.519800               0.832200  0.441600   
11         0.703300      0.604800  0.650300               0.673200  0.622200   
12         0.839000      0.301800  0.443900               0.578800  0.346100   
13         0.624700      0.912300  0.741600               0.664400  0.835400   
14         0.641200      0.678500  0.659300               0.649100  0.670700   
15         0.683900      0.619400  0.650100               0.665800  0.631300   
16         0.214900      0.131500  0.163200               0.299100  0.142600   
17         0.510800      0.905500  0.653200               0.434800  0.784300   
18         0.624400      0.898200  0.736

In [67]:
from imblearn.combine import SMOTEENN
from collections import Counter

counter = Counter(y_train)
print('Before', counter)

enn = SMOTEENN(random_state=10)
X_train_enn, y_train_enn = enn.fit_resample(X_train, y_train)

counter = Counter(y_train_enn)
print('After', counter)

Before Counter({0: 61743, 1: 15623})
After Counter({1: 36142, 0: 35246})


In [68]:
lr_pipeline = Pipeline([
    ('lr_model', LogisticRegression(**rsearch_lr.best_params_))
])

In [69]:
dt_pipeline = Pipeline([
    ('dt_model', DecisionTreeClassifier(**rsearch_dt.best_params_,random_state=42))
])

In [70]:
rf_pipeline = Pipeline([
    ('rf_model', RandomForestClassifier(**rsearch_rf.best_params_,random_state=42))
])

In [71]:
gnb_pipeline = Pipeline([
    ('gnb_model', GaussianNB())
])

In [72]:
bnb_pipeline = Pipeline([
    ('bnb_model', BernoulliNB())
])

In [73]:
knn_pipeline = Pipeline([
    ('knn_model', KNeighborsClassifier())
])

In [74]:
ada_pipeline = Pipeline([
    ('ada_model', AdaBoostClassifier(**rsearch_ada.best_params_, random_state = 42))
])

In [75]:
gb_pipeline = Pipeline([
    ('gb_model', GradientBoostingClassifier(**rsearch_gb.best_params_, random_state = 42))
])

In [76]:
cb_pipeline = Pipeline([
    ('cb_model', CatBoostClassifier(**rsearch_cb.best_params_, random_state = 42))
])

In [77]:
lgbm_pipeline = Pipeline([
    ('lgbm_model', LGBMClassifier(**rsearch_lgbm.best_params_, random_state = 42))
])

In [78]:
xgb_pipeline = Pipeline([
    ('xgb_model', XGBClassifier(**rsearch_xgb.best_params_, random_state = 42))
])

In [79]:
pipe_all = [lr_pipeline, dt_pipeline, rf_pipeline, gnb_pipeline, bnb_pipeline, ada_pipeline, gb_pipeline, xgb_pipeline, cb_pipeline, lgbm_pipeline,
            knn_pipeline]
            
for pipe in pipe_all:
  pipe.fit(X_train_enn, y_train_enn)

0:	learn: 0.3933076	total: 10.6ms	remaining: 2.03s
1:	learn: 0.3379358	total: 20.2ms	remaining: 1.92s
2:	learn: 0.3120347	total: 29.8ms	remaining: 1.89s
3:	learn: 0.3017062	total: 38.9ms	remaining: 1.84s
4:	learn: 0.2953433	total: 47.6ms	remaining: 1.79s
5:	learn: 0.2901686	total: 56.7ms	remaining: 1.77s
6:	learn: 0.2831599	total: 65.5ms	remaining: 1.74s
7:	learn: 0.2794640	total: 74.5ms	remaining: 1.72s
8:	learn: 0.2763037	total: 82.9ms	remaining: 1.7s
9:	learn: 0.2730971	total: 91.9ms	remaining: 1.68s
10:	learn: 0.2661423	total: 101ms	remaining: 1.67s
11:	learn: 0.2646149	total: 109ms	remaining: 1.65s
12:	learn: 0.2578237	total: 118ms	remaining: 1.63s
13:	learn: 0.2537464	total: 126ms	remaining: 1.61s
14:	learn: 0.2516321	total: 135ms	remaining: 1.6s
15:	learn: 0.2462203	total: 143ms	remaining: 1.58s
16:	learn: 0.2380691	total: 152ms	remaining: 1.57s
17:	learn: 0.2331970	total: 160ms	remaining: 1.56s
18:	learn: 0.2293912	total: 169ms	remaining: 1.54s
19:	learn: 0.2266074	total: 177ms

175:	learn: 0.1044599	total: 1.51s	remaining: 146ms
176:	learn: 0.1041595	total: 1.52s	remaining: 137ms
177:	learn: 0.1038251	total: 1.52s	remaining: 129ms
178:	learn: 0.1032084	total: 1.53s	remaining: 120ms
179:	learn: 0.1029824	total: 1.54s	remaining: 111ms
180:	learn: 0.1028604	total: 1.55s	remaining: 103ms
181:	learn: 0.1026001	total: 1.56s	remaining: 94.2ms
182:	learn: 0.1023269	total: 1.57s	remaining: 85.6ms
183:	learn: 0.1019616	total: 1.57s	remaining: 77.1ms
184:	learn: 0.1017178	total: 1.58s	remaining: 68.5ms
185:	learn: 0.1011997	total: 1.59s	remaining: 60ms
186:	learn: 0.1010502	total: 1.6s	remaining: 51.4ms
187:	learn: 0.1005309	total: 1.61s	remaining: 42.8ms
188:	learn: 0.1003148	total: 1.62s	remaining: 34.3ms
189:	learn: 0.0997957	total: 1.63s	remaining: 25.7ms
190:	learn: 0.0995860	total: 1.64s	remaining: 17.1ms
191:	learn: 0.0994462	total: 1.64s	remaining: 8.57ms
192:	learn: 0.0993317	total: 1.65s	remaining: 0us


In [80]:
for model in pipe_all:
    
    model_scores['Model Name'].append(str(model[0]).split('(')[0] + " ENN")
    
    model_scores['Accuracy train'].append(model.score(X_train_enn, y_train_enn))
    pred_tr = model.predict(X_train_enn)
    prob_tr = model.predict_proba(X_train_enn)[:,1]
    model_scores['Precision train'].append(precision_score(y_train_enn, pred_tr))
    model_scores['Recall train'].append(recall_score(y_train_enn, pred_tr))
    model_scores['F1 train'].append(f1_score(y_train_enn, pred_tr))
    model_scores['F1 Avg Weighted train'].append(f1_score(y_train_enn, pred_tr, average = 'weighted'))
    model_scores['F2 train'].append(fbeta_score(y_train_enn, pred_tr, beta = 2.0))
    model_scores['ROC AUC train'].append(roc_auc_score(y_train_enn, prob_tr))
    
    model_scores['Accuracy test'].append(model.score(X_test, y_test))
    pred_ts = model.predict(X_test)
    prob_ts = model.predict_proba(X_test)[:,1]
    model_scores['Precision test'].append(precision_score(y_test, pred_ts))
    model_scores['Recall test'].append(recall_score(y_test, pred_ts))
    model_scores['F1 test'].append(f1_score(y_test, pred_ts))
    model_scores['F1 Avg Weighted test'].append(f1_score(y_test, pred_ts, average = 'weighted'))
    model_scores['F2 test'].append(fbeta_score(y_test, pred_ts, beta = 2.0))
    model_scores['ROC AUC test'].append(roc_auc_score(y_test, prob_ts))

    model_scores['CV-5-Mean'].append(cross_val_score(model,X_train_enn,y_train_enn,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring=my_f2_scorer()).mean())
    model_scores['CV-5-SD'].append(cross_val_score(model,X_train_enn,y_train_enn,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring=my_f2_scorer()).std())

0:	learn: 0.3949851	total: 15.5ms	remaining: 2.97s
1:	learn: 0.3387745	total: 24.9ms	remaining: 2.38s
2:	learn: 0.3142336	total: 33.9ms	remaining: 2.15s
3:	learn: 0.3045094	total: 42.8ms	remaining: 2.02s
4:	learn: 0.2976372	total: 51.3ms	remaining: 1.93s
5:	learn: 0.2882813	total: 60.6ms	remaining: 1.89s
6:	learn: 0.2806097	total: 69.5ms	remaining: 1.85s
7:	learn: 0.2757293	total: 78ms	remaining: 1.8s
8:	learn: 0.2698304	total: 86.7ms	remaining: 1.77s
9:	learn: 0.2615744	total: 95.7ms	remaining: 1.75s
10:	learn: 0.2575182	total: 105ms	remaining: 1.73s
11:	learn: 0.2556328	total: 112ms	remaining: 1.7s
12:	learn: 0.2515598	total: 121ms	remaining: 1.67s
13:	learn: 0.2489208	total: 129ms	remaining: 1.64s
14:	learn: 0.2453337	total: 137ms	remaining: 1.63s
15:	learn: 0.2411002	total: 145ms	remaining: 1.6s
16:	learn: 0.2357933	total: 153ms	remaining: 1.58s
17:	learn: 0.2315552	total: 161ms	remaining: 1.56s
18:	learn: 0.2290090	total: 169ms	remaining: 1.55s
19:	learn: 0.2266389	total: 177ms	re

161:	learn: 0.1088198	total: 1.32s	remaining: 254ms
162:	learn: 0.1085040	total: 1.33s	remaining: 245ms
163:	learn: 0.1080661	total: 1.34s	remaining: 237ms
164:	learn: 0.1076591	total: 1.35s	remaining: 229ms
165:	learn: 0.1074431	total: 1.36s	remaining: 221ms
166:	learn: 0.1066673	total: 1.36s	remaining: 212ms
167:	learn: 0.1062831	total: 1.37s	remaining: 204ms
168:	learn: 0.1052473	total: 1.38s	remaining: 196ms
169:	learn: 0.1050464	total: 1.39s	remaining: 188ms
170:	learn: 0.1046984	total: 1.4s	remaining: 180ms
171:	learn: 0.1044342	total: 1.4s	remaining: 171ms
172:	learn: 0.1040334	total: 1.41s	remaining: 163ms
173:	learn: 0.1036066	total: 1.42s	remaining: 155ms
174:	learn: 0.1031955	total: 1.43s	remaining: 147ms
175:	learn: 0.1028799	total: 1.44s	remaining: 139ms
176:	learn: 0.1023241	total: 1.45s	remaining: 131ms
177:	learn: 0.1021201	total: 1.45s	remaining: 122ms
178:	learn: 0.1018877	total: 1.46s	remaining: 114ms
179:	learn: 0.1017121	total: 1.47s	remaining: 106ms
180:	learn: 0.

141:	learn: 0.1141874	total: 1.15s	remaining: 414ms
142:	learn: 0.1137810	total: 1.16s	remaining: 406ms
143:	learn: 0.1128006	total: 1.17s	remaining: 398ms
144:	learn: 0.1122983	total: 1.18s	remaining: 390ms
145:	learn: 0.1119466	total: 1.18s	remaining: 381ms
146:	learn: 0.1117281	total: 1.19s	remaining: 373ms
147:	learn: 0.1114183	total: 1.2s	remaining: 365ms
148:	learn: 0.1110501	total: 1.21s	remaining: 357ms
149:	learn: 0.1108490	total: 1.22s	remaining: 349ms
150:	learn: 0.1107074	total: 1.23s	remaining: 341ms
151:	learn: 0.1104769	total: 1.23s	remaining: 333ms
152:	learn: 0.1102135	total: 1.24s	remaining: 324ms
153:	learn: 0.1098568	total: 1.25s	remaining: 316ms
154:	learn: 0.1095712	total: 1.26s	remaining: 308ms
155:	learn: 0.1092600	total: 1.26s	remaining: 300ms
156:	learn: 0.1088813	total: 1.27s	remaining: 292ms
157:	learn: 0.1085288	total: 1.28s	remaining: 284ms
158:	learn: 0.1083930	total: 1.29s	remaining: 275ms
159:	learn: 0.1081504	total: 1.3s	remaining: 267ms
160:	learn: 0.

114:	learn: 0.1296984	total: 939ms	remaining: 637ms
115:	learn: 0.1284037	total: 948ms	remaining: 629ms
116:	learn: 0.1278508	total: 956ms	remaining: 621ms
117:	learn: 0.1276215	total: 964ms	remaining: 613ms
118:	learn: 0.1271178	total: 972ms	remaining: 604ms
119:	learn: 0.1269124	total: 980ms	remaining: 596ms
120:	learn: 0.1262684	total: 987ms	remaining: 588ms
121:	learn: 0.1259947	total: 995ms	remaining: 579ms
122:	learn: 0.1254962	total: 1s	remaining: 571ms
123:	learn: 0.1249667	total: 1.01s	remaining: 563ms
124:	learn: 0.1245436	total: 1.02s	remaining: 554ms
125:	learn: 0.1242149	total: 1.03s	remaining: 546ms
126:	learn: 0.1236414	total: 1.03s	remaining: 538ms
127:	learn: 0.1232439	total: 1.04s	remaining: 530ms
128:	learn: 0.1229718	total: 1.05s	remaining: 521ms
129:	learn: 0.1227069	total: 1.06s	remaining: 513ms
130:	learn: 0.1222573	total: 1.07s	remaining: 505ms
131:	learn: 0.1221028	total: 1.07s	remaining: 497ms
132:	learn: 0.1216165	total: 1.08s	remaining: 488ms
133:	learn: 0.1

92:	learn: 0.1395739	total: 767ms	remaining: 825ms
93:	learn: 0.1387203	total: 775ms	remaining: 817ms
94:	learn: 0.1381356	total: 783ms	remaining: 808ms
95:	learn: 0.1375106	total: 791ms	remaining: 800ms
96:	learn: 0.1369606	total: 799ms	remaining: 791ms
97:	learn: 0.1360243	total: 808ms	remaining: 783ms
98:	learn: 0.1349949	total: 816ms	remaining: 774ms
99:	learn: 0.1341513	total: 823ms	remaining: 766ms
100:	learn: 0.1335855	total: 832ms	remaining: 758ms
101:	learn: 0.1330250	total: 840ms	remaining: 749ms
102:	learn: 0.1324667	total: 848ms	remaining: 741ms
103:	learn: 0.1320529	total: 855ms	remaining: 732ms
104:	learn: 0.1314502	total: 863ms	remaining: 724ms
105:	learn: 0.1310762	total: 871ms	remaining: 715ms
106:	learn: 0.1307710	total: 880ms	remaining: 707ms
107:	learn: 0.1305568	total: 887ms	remaining: 698ms
108:	learn: 0.1299209	total: 895ms	remaining: 690ms
109:	learn: 0.1295104	total: 903ms	remaining: 681ms
110:	learn: 0.1290883	total: 911ms	remaining: 673ms
111:	learn: 0.128338

...

22:	learn: 0.2192950	total: 209ms	remaining: 1.54s
23:	learn: 0.2165916	total: 216ms	remaining: 1.52s
24:	learn: 0.2148514	total: 225ms	remaining: 1.51s
25:	learn: 0.2107903	total: 233ms	remaining: 1.49s
26:	learn: 0.2083594	total: 241ms	remaining: 1.48s
27:	learn: 0.2067675	total: 249ms	remaining: 1.47s
28:	learn: 0.2047625	total: 256ms	remaining: 1.45s
29:	learn: 0.2031327	total: 264ms	remaining: 1.44s
30:	learn: 0.2014282	total: 272ms	remaining: 1.42s
31:	learn: 0.1992112	total: 280ms	remaining: 1.41s
32:	learn: 0.1978559	total: 288ms	remaining: 1.4s
33:	learn: 0.1965154	total: 296ms	remaining: 1.38s
34:	learn: 0.1950236	total: 304ms	remaining: 1.37s
35:	learn: 0.1924213	total: 312ms	remaining: 1.36s
36:	learn: 0.1909406	total: 320ms	remaining: 1.35s
37:	learn: 0.1902716	total: 328ms	remaining: 1.34s
38:	learn: 0.1882962	total: 336ms	remaining: 1.32s
39:	learn: 0.1866574	total: 344ms	remaining: 1.31s
40:	learn: 0.1855561	total: 352ms	remaining: 1.3s
41:	learn: 0.1827845	total: 360ms

0:	learn: 0.3941501	total: 24.1ms	remaining: 4.62s
1:	learn: 0.3391940	total: 33ms	remaining: 3.15s
2:	learn: 0.3142165	total: 41.3ms	remaining: 2.62s
3:	learn: 0.3022751	total: 49.3ms	remaining: 2.33s
4:	learn: 0.2947679	total: 57.5ms	remaining: 2.16s
5:	learn: 0.2889729	total: 65.7ms	remaining: 2.05s
6:	learn: 0.2849915	total: 74.6ms	remaining: 1.98s
7:	learn: 0.2771258	total: 84.4ms	remaining: 1.95s
8:	learn: 0.2726312	total: 93.4ms	remaining: 1.91s
9:	learn: 0.2626007	total: 103ms	remaining: 1.88s
10:	learn: 0.2590330	total: 111ms	remaining: 1.84s
11:	learn: 0.2542704	total: 120ms	remaining: 1.8s
12:	learn: 0.2512077	total: 128ms	remaining: 1.78s
13:	learn: 0.2484846	total: 137ms	remaining: 1.75s
14:	learn: 0.2442307	total: 144ms	remaining: 1.71s
15:	learn: 0.2401052	total: 152ms	remaining: 1.68s
16:	learn: 0.2345175	total: 160ms	remaining: 1.66s
17:	learn: 0.2312161	total: 168ms	remaining: 1.64s
18:	learn: 0.2271376	total: 177ms	remaining: 1.62s
19:	learn: 0.2233316	total: 185ms	r

161:	learn: 0.1110250	total: 1.32s	remaining: 253ms
162:	learn: 0.1106274	total: 1.33s	remaining: 245ms
163:	learn: 0.1102784	total: 1.34s	remaining: 237ms
164:	learn: 0.1101283	total: 1.35s	remaining: 229ms
165:	learn: 0.1097536	total: 1.35s	remaining: 220ms
166:	learn: 0.1096130	total: 1.36s	remaining: 212ms
167:	learn: 0.1091243	total: 1.37s	remaining: 204ms
168:	learn: 0.1088445	total: 1.38s	remaining: 196ms
169:	learn: 0.1083835	total: 1.39s	remaining: 188ms
170:	learn: 0.1079361	total: 1.39s	remaining: 179ms
171:	learn: 0.1073615	total: 1.4s	remaining: 171ms
172:	learn: 0.1071018	total: 1.41s	remaining: 163ms
173:	learn: 0.1068933	total: 1.42s	remaining: 155ms
174:	learn: 0.1062865	total: 1.43s	remaining: 147ms
175:	learn: 0.1058813	total: 1.43s	remaining: 139ms
176:	learn: 0.1057048	total: 1.44s	remaining: 130ms
177:	learn: 0.1054891	total: 1.45s	remaining: 122ms
178:	learn: 0.1053642	total: 1.46s	remaining: 114ms
179:	learn: 0.1049994	total: 1.47s	remaining: 106ms
180:	learn: 0

138:	learn: 0.1152013	total: 1.13s	remaining: 439ms
139:	learn: 0.1148774	total: 1.14s	remaining: 430ms
140:	learn: 0.1146575	total: 1.14s	remaining: 422ms
141:	learn: 0.1142552	total: 1.15s	remaining: 414ms
142:	learn: 0.1139489	total: 1.16s	remaining: 406ms
143:	learn: 0.1132663	total: 1.17s	remaining: 398ms
144:	learn: 0.1128179	total: 1.18s	remaining: 389ms
145:	learn: 0.1124742	total: 1.18s	remaining: 381ms
146:	learn: 0.1116562	total: 1.19s	remaining: 373ms
147:	learn: 0.1110054	total: 1.2s	remaining: 365ms
148:	learn: 0.1108109	total: 1.21s	remaining: 357ms
149:	learn: 0.1103159	total: 1.22s	remaining: 349ms
150:	learn: 0.1098017	total: 1.23s	remaining: 341ms
151:	learn: 0.1093864	total: 1.23s	remaining: 333ms
152:	learn: 0.1089702	total: 1.24s	remaining: 325ms
153:	learn: 0.1084715	total: 1.25s	remaining: 316ms
154:	learn: 0.1079540	total: 1.26s	remaining: 308ms
155:	learn: 0.1075144	total: 1.26s	remaining: 300ms
156:	learn: 0.1069481	total: 1.27s	remaining: 292ms
157:	learn: 0

117:	learn: 0.1243173	total: 961ms	remaining: 611ms
118:	learn: 0.1236782	total: 969ms	remaining: 603ms
119:	learn: 0.1231150	total: 977ms	remaining: 595ms
120:	learn: 0.1226078	total: 985ms	remaining: 586ms
121:	learn: 0.1220320	total: 994ms	remaining: 578ms
122:	learn: 0.1209510	total: 1s	remaining: 570ms
123:	learn: 0.1206669	total: 1.01s	remaining: 562ms
124:	learn: 0.1203161	total: 1.02s	remaining: 554ms
125:	learn: 0.1199831	total: 1.02s	remaining: 545ms
126:	learn: 0.1195290	total: 1.03s	remaining: 537ms
127:	learn: 0.1192509	total: 1.04s	remaining: 529ms
128:	learn: 0.1189667	total: 1.05s	remaining: 521ms
129:	learn: 0.1184003	total: 1.06s	remaining: 512ms
130:	learn: 0.1181041	total: 1.06s	remaining: 504ms
131:	learn: 0.1175429	total: 1.07s	remaining: 496ms
132:	learn: 0.1172751	total: 1.08s	remaining: 488ms
133:	learn: 0.1170105	total: 1.09s	remaining: 480ms
134:	learn: 0.1162448	total: 1.1s	remaining: 472ms
135:	learn: 0.1160844	total: 1.1s	remaining: 463ms
136:	learn: 0.115

In [81]:
pd.DataFrame(model_scores).round(4)

Model Name  Accuracy train  \
0                                  LogisticRegression        0.819900   
1                              DecisionTreeClassifier        0.811700   
2                              RandomForestClassifier        0.825000   
3                                          GaussianNB        0.791100   
4                                         BernoulliNB        0.819500   
5                                  AdaBoostClassifier        0.201900   
6                          GradientBoostingClassifier        0.276200   
7                                       XGBClassifier        0.754400   
8   <catboost.core.CatBoostClassifier object at 0x...        0.859400   
9                                      LGBMClassifier        0.574300   
10                               KNeighborsClassifier        0.850200   
11                           LogisticRegression SMOTE        0.674800   
12                       DecisionTreeClassifier SMOTE        0.621900   
13                       RandomForestClassifier SMOTE        0.682200   
14                                   GaussianNB SMOTE        0.649400   
15                                  BernoulliNB SMOTE        0.666600   
16                           AdaBoostClassifier SMOTE        0.325500   
17                   GradientBoostingClassifier SMOTE        0.519200   
18                                XGBClassifier SMOTE        0.678900   
19  <catboost.core.CatBoostClassifier object at 0x...        0.896400   
20                               LGBMClassifier SMOTE        0.446600   
21                         KNeighborsClassifier SMOTE        0.846600   
22                          LogisticRegression ADASYN        0.646700   
23                      DecisionTreeClassifier ADASYN        0.568200   
24                      RandomForestClassifier ADASYN        0.681900   
25                                  GaussianNB ADASYN        0.580200   
26                                 BernoulliNB ADASYN        0.647000   
27                          AdaBoostClassifier ADASYN        0.322800   
28                  GradientBoostingClassifier ADASYN        0.642400   
29                               XGBClassifier ADASYN        0.592300   
30  <catboost.core.CatBoostClassifier object at 0x...        0.895900   
31                              LGBMClassifier ADASYN        0.512200   
32                        KNeighborsClassifier ADASYN        0.834400   
33                             LogisticRegression ENN        0.798200   
34                         DecisionTreeClassifier ENN        0.697100   
35                         RandomForestClassifier ENN        0.797700   
36                                     GaussianNB ENN        0.765200   
37                                    BernoulliNB ENN        0.780900   
38                             AdaBoostClassifier ENN        0.219400   
39                     GradientBoostingClassifier ENN        0.579900   
40                                  XGBClassifier ENN        0.794500   
41  <catboost.core.CatBoostClassifier object at 0x...        0.965500   
42                                 LGBMClassifier ENN        0.502000   
43                           KNeighborsClassifier ENN        0.976300   

    Precision train  Recall train  F1 train  F1 Avg Weighted train  F2 train  \
0          0.758000      0.158800  0.262600               0.769200  0.188600   
1          0.564400      0.296500  0.388800               0.787800  0.327600   
2          0.691800      0.240800  0.357200               0.789400  0.276900   
3          0.472400      0.292600  0.361400               0.771400  0.316700   
4          0.685800      0.195700  0.304600               0.776800  0.228400   
5          0.201900      1.000000  0.336000               0.067900  0.558500   
6          0.203400      0.886300  0.330900               0.235800  0.530300   
7          0.398900      0.426000  0.412000               0.757400  0.420300   
8          0.839100      0.375500  0.

In [82]:
from imblearn.combine import SMOTEENN
from collections import Counter
from imblearn.under_sampling import EditedNearestNeighbours

counter = Counter(y_train)
print('Before', counter)

smote = SMOTE(random_state=10)
enn = EditedNearestNeighbours()

se = SMOTEENN(random_state=10, smote=smote, enn=enn)
X_train_se, y_train_se = se.fit_resample(X_train, y_train)

counter = Counter(y_train_se)
print('After', counter)

Before Counter({0: 61743, 1: 15623})
After Counter({0: 61743, 1: 36142})


In [83]:
lr_pipeline = Pipeline([
    ('lr_model', LogisticRegression(**rsearch_lr.best_params_))
])

In [84]:
dt_pipeline = Pipeline([
    ('dt_model', DecisionTreeClassifier(**rsearch_dt.best_params_,random_state=42))
])

In [85]:
rf_pipeline = Pipeline([
    ('rf_model', RandomForestClassifier(**rsearch_rf.best_params_,random_state=42))
])

In [86]:
gnb_pipeline = Pipeline([
    ('gnb_model', GaussianNB())
])

In [87]:
bnb_pipeline = Pipeline([
    ('bnb_model', BernoulliNB())
])

In [88]:
knn_pipeline = Pipeline([
    ('knn_model', KNeighborsClassifier())
])

In [89]:
ada_pipeline = Pipeline([
    ('ada_model', AdaBoostClassifier(**rsearch_ada.best_params_, random_state = 42))
])

In [90]:
gb_pipeline = Pipeline([
    ('gb_model', GradientBoostingClassifier(**rsearch_gb.best_params_, random_state = 42))
])

In [91]:
cb_pipeline = Pipeline([
    ('cb_model', CatBoostClassifier(**rsearch_cb.best_params_, random_state = 42))
])

In [92]:
lgbm_pipeline = Pipeline([
    ('lgbm_model', LGBMClassifier(**rsearch_lgbm.best_params_, random_state = 42))
])

In [93]:
xgb_pipeline = Pipeline([
    ('xgb_model', XGBClassifier(**rsearch_xgb.best_params_, random_state = 42))
])

In [94]:
pipe_all = [lr_pipeline, dt_pipeline, rf_pipeline, gnb_pipeline, bnb_pipeline, ada_pipeline, gb_pipeline, xgb_pipeline, cb_pipeline, lgbm_pipeline,
            knn_pipeline]
            
for pipe in pipe_all:
  pipe.fit(X_train_se, y_train_se)

0:	learn: 0.4623782	total: 15.6ms	remaining: 2.98s
1:	learn: 0.4150181	total: 26.2ms	remaining: 2.5s
2:	learn: 0.3993533	total: 36ms	remaining: 2.28s
3:	learn: 0.3909121	total: 45.5ms	remaining: 2.15s
4:	learn: 0.3847082	total: 55.1ms	remaining: 2.07s
5:	learn: 0.3811603	total: 64.2ms	remaining: 2s
6:	learn: 0.3601275	total: 74.3ms	remaining: 1.98s
7:	learn: 0.3522255	total: 84.2ms	remaining: 1.95s
8:	learn: 0.3473163	total: 93.2ms	remaining: 1.91s
9:	learn: 0.3340743	total: 103ms	remaining: 1.88s
10:	learn: 0.3301863	total: 112ms	remaining: 1.85s
11:	learn: 0.3236974	total: 121ms	remaining: 1.83s
12:	learn: 0.3188389	total: 130ms	remaining: 1.8s
13:	learn: 0.3132925	total: 140ms	remaining: 1.78s
14:	learn: 0.3096374	total: 149ms	remaining: 1.77s
15:	learn: 0.3029670	total: 158ms	remaining: 1.75s
16:	learn: 0.2993646	total: 168ms	remaining: 1.74s
17:	learn: 0.2963693	total: 177ms	remaining: 1.72s
18:	learn: 0.2923957	total: 186ms	remaining: 1.7s
19:	learn: 0.2862968	total: 196ms	remain

180:	learn: 0.1578416	total: 1.74s	remaining: 115ms
181:	learn: 0.1576537	total: 1.75s	remaining: 106ms
182:	learn: 0.1573945	total: 1.76s	remaining: 96.2ms
183:	learn: 0.1571809	total: 1.77s	remaining: 86.6ms
184:	learn: 0.1569773	total: 1.78s	remaining: 77ms
185:	learn: 0.1566943	total: 1.79s	remaining: 67.4ms
186:	learn: 0.1564973	total: 1.8s	remaining: 57.8ms
187:	learn: 0.1563318	total: 1.81s	remaining: 48.1ms
188:	learn: 0.1561341	total: 1.82s	remaining: 38.5ms
189:	learn: 0.1559397	total: 1.83s	remaining: 28.9ms
190:	learn: 0.1557482	total: 1.84s	remaining: 19.3ms
191:	learn: 0.1553734	total: 1.85s	remaining: 9.64ms
192:	learn: 0.1551880	total: 1.86s	remaining: 0us


In [95]:
for model in pipe_all:
    
    model_scores['Model Name'].append(str(model[0]).split('(')[0] + " SMOTE + ENN")
    
    model_scores['Accuracy train'].append(model.score(X_train_se, y_train_se))
    pred_tr = model.predict(X_train_se)
    prob_tr = model.predict_proba(X_train_se)[:,1]
    model_scores['Precision train'].append(precision_score(y_train_se, pred_tr))
    model_scores['Recall train'].append(recall_score(y_train_se, pred_tr))
    model_scores['F1 train'].append(f1_score(y_train_se, pred_tr))
    model_scores['F1 Avg Weighted train'].append(f1_score(y_train_se, pred_tr, average = 'weighted'))
    model_scores['F2 train'].append(fbeta_score(y_train_se, pred_tr, beta = 2.0))
    model_scores['ROC AUC train'].append(roc_auc_score(y_train_se, prob_tr))
    
    model_scores['Accuracy test'].append(model.score(X_test, y_test))
    pred_ts = model.predict(X_test)
    prob_ts = model.predict_proba(X_test)[:,1]
    model_scores['Precision test'].append(precision_score(y_test, pred_ts))
    model_scores['Recall test'].append(recall_score(y_test, pred_ts))
    model_scores['F1 test'].append(f1_score(y_test, pred_ts))
    model_scores['F1 Avg Weighted test'].append(f1_score(y_test, pred_ts, average = 'weighted'))
    model_scores['F2 test'].append(fbeta_score(y_test, pred_ts, beta = 2.0))
    model_scores['ROC AUC test'].append(roc_auc_score(y_test, prob_ts))

    model_scores['CV-5-Mean'].append(cross_val_score(model,X_train_se,y_train_se,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring=my_f2_scorer()).mean())
    model_scores['CV-5-SD'].append(cross_val_score(model,X_train_se,y_train_se,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring=my_f2_scorer()).std())

0:	learn: 0.4677469	total: 16.9ms	remaining: 3.25s
1:	learn: 0.4188854	total: 26.8ms	remaining: 2.56s
2:	learn: 0.3928662	total: 36.2ms	remaining: 2.29s
3:	learn: 0.3822604	total: 45.1ms	remaining: 2.13s
4:	learn: 0.3706163	total: 53.9ms	remaining: 2.02s
5:	learn: 0.3675721	total: 62.8ms	remaining: 1.96s
6:	learn: 0.3588825	total: 71.7ms	remaining: 1.91s
7:	learn: 0.3549429	total: 80.9ms	remaining: 1.87s
8:	learn: 0.3530313	total: 89.6ms	remaining: 1.83s
9:	learn: 0.3403979	total: 98.5ms	remaining: 1.8s
10:	learn: 0.3372967	total: 107ms	remaining: 1.78s
11:	learn: 0.3331606	total: 116ms	remaining: 1.75s
12:	learn: 0.3261170	total: 124ms	remaining: 1.72s
13:	learn: 0.3182516	total: 133ms	remaining: 1.7s
14:	learn: 0.3144862	total: 141ms	remaining: 1.68s
15:	learn: 0.3098320	total: 150ms	remaining: 1.66s
16:	learn: 0.3039540	total: 158ms	remaining: 1.64s
17:	learn: 0.2955797	total: 167ms	remaining: 1.63s
18:	learn: 0.2923055	total: 176ms	remaining: 1.61s
19:	learn: 0.2887968	total: 184ms

169:	learn: 0.1611081	total: 1.51s	remaining: 205ms
170:	learn: 0.1606971	total: 1.52s	remaining: 196ms
171:	learn: 0.1603670	total: 1.53s	remaining: 187ms
172:	learn: 0.1602142	total: 1.54s	remaining: 178ms
173:	learn: 0.1597656	total: 1.55s	remaining: 169ms
174:	learn: 0.1596321	total: 1.56s	remaining: 160ms
175:	learn: 0.1593503	total: 1.57s	remaining: 151ms
176:	learn: 0.1590992	total: 1.57s	remaining: 142ms
177:	learn: 0.1585852	total: 1.58s	remaining: 133ms
178:	learn: 0.1584287	total: 1.59s	remaining: 125ms
179:	learn: 0.1580447	total: 1.6s	remaining: 116ms
180:	learn: 0.1578817	total: 1.61s	remaining: 107ms
181:	learn: 0.1575620	total: 1.62s	remaining: 97.8ms
182:	learn: 0.1572401	total: 1.63s	remaining: 88.9ms
183:	learn: 0.1570701	total: 1.63s	remaining: 80ms
184:	learn: 0.1567558	total: 1.64s	remaining: 71.1ms
185:	learn: 0.1565672	total: 1.65s	remaining: 62.2ms
186:	learn: 0.1563336	total: 1.66s	remaining: 53.3ms
187:	learn: 0.1558937	total: 1.67s	remaining: 44.4ms
188:	lea

151:	learn: 0.1652511	total: 1.34s	remaining: 362ms
152:	learn: 0.1649119	total: 1.35s	remaining: 353ms
153:	learn: 0.1645021	total: 1.36s	remaining: 344ms
154:	learn: 0.1641907	total: 1.37s	remaining: 335ms
155:	learn: 0.1638299	total: 1.38s	remaining: 326ms
156:	learn: 0.1635416	total: 1.38s	remaining: 317ms
157:	learn: 0.1633405	total: 1.39s	remaining: 308ms
158:	learn: 0.1629971	total: 1.4s	remaining: 300ms
159:	learn: 0.1623862	total: 1.41s	remaining: 291ms
160:	learn: 0.1620299	total: 1.42s	remaining: 282ms
161:	learn: 0.1616067	total: 1.43s	remaining: 273ms
162:	learn: 0.1612161	total: 1.44s	remaining: 264ms
163:	learn: 0.1609386	total: 1.45s	remaining: 256ms
164:	learn: 0.1606734	total: 1.45s	remaining: 247ms
165:	learn: 0.1603188	total: 1.46s	remaining: 238ms
166:	learn: 0.1599926	total: 1.47s	remaining: 229ms
167:	learn: 0.1597460	total: 1.48s	remaining: 220ms
168:	learn: 0.1594016	total: 1.49s	remaining: 211ms
169:	learn: 0.1589214	total: 1.5s	remaining: 203ms
170:	learn: 0.

127:	learn: 0.1722416	total: 1.15s	remaining: 585ms
128:	learn: 0.1717755	total: 1.16s	remaining: 576ms
129:	learn: 0.1713976	total: 1.17s	remaining: 566ms
130:	learn: 0.1711684	total: 1.18s	remaining: 557ms
131:	learn: 0.1708745	total: 1.19s	remaining: 548ms
132:	learn: 0.1703825	total: 1.2s	remaining: 539ms
133:	learn: 0.1699608	total: 1.2s	remaining: 530ms
134:	learn: 0.1696546	total: 1.21s	remaining: 521ms
135:	learn: 0.1691389	total: 1.22s	remaining: 512ms
136:	learn: 0.1686065	total: 1.23s	remaining: 503ms
137:	learn: 0.1681792	total: 1.24s	remaining: 494ms
138:	learn: 0.1677344	total: 1.25s	remaining: 485ms
139:	learn: 0.1674736	total: 1.26s	remaining: 476ms
140:	learn: 0.1670587	total: 1.26s	remaining: 467ms
141:	learn: 0.1665316	total: 1.27s	remaining: 458ms
142:	learn: 0.1663819	total: 1.28s	remaining: 449ms
143:	learn: 0.1659255	total: 1.29s	remaining: 440ms
144:	learn: 0.1656275	total: 1.3s	remaining: 431ms
145:	learn: 0.1654105	total: 1.31s	remaining: 421ms
146:	learn: 0.1

106:	learn: 0.1835923	total: 954ms	remaining: 767ms
107:	learn: 0.1831322	total: 963ms	remaining: 758ms
108:	learn: 0.1826710	total: 972ms	remaining: 749ms
109:	learn: 0.1822592	total: 980ms	remaining: 740ms
110:	learn: 0.1819387	total: 989ms	remaining: 730ms
111:	learn: 0.1814905	total: 997ms	remaining: 721ms
112:	learn: 0.1811959	total: 1s	remaining: 712ms
113:	learn: 0.1808298	total: 1.01s	remaining: 703ms
114:	learn: 0.1802048	total: 1.02s	remaining: 694ms
115:	learn: 0.1797439	total: 1.03s	remaining: 685ms
116:	learn: 0.1795177	total: 1.04s	remaining: 676ms
117:	learn: 0.1791067	total: 1.05s	remaining: 667ms
118:	learn: 0.1789169	total: 1.06s	remaining: 658ms
119:	learn: 0.1787363	total: 1.07s	remaining: 649ms
120:	learn: 0.1784738	total: 1.07s	remaining: 640ms
121:	learn: 0.1782721	total: 1.08s	remaining: 631ms
122:	learn: 0.1775126	total: 1.09s	remaining: 622ms
123:	learn: 0.1771339	total: 1.1s	remaining: 613ms
124:	learn: 0.1767704	total: 1.11s	remaining: 604ms
125:	learn: 0.17

...

43:	learn: 0.2311394	total: 388ms	remaining: 1.31s
44:	learn: 0.2298745	total: 397ms	remaining: 1.3s
45:	learn: 0.2273672	total: 406ms	remaining: 1.3s
46:	learn: 0.2255077	total: 415ms	remaining: 1.29s
47:	learn: 0.2246043	total: 424ms	remaining: 1.28s
48:	learn: 0.2232961	total: 432ms	remaining: 1.27s
49:	learn: 0.2211881	total: 441ms	remaining: 1.26s
50:	learn: 0.2203983	total: 450ms	remaining: 1.25s
51:	learn: 0.2197939	total: 458ms	remaining: 1.24s
52:	learn: 0.2181063	total: 467ms	remaining: 1.23s
53:	learn: 0.2174551	total: 476ms	remaining: 1.22s
54:	learn: 0.2165215	total: 484ms	remaining: 1.21s
55:	learn: 0.2155426	total: 493ms	remaining: 1.21s
56:	learn: 0.2148402	total: 501ms	remaining: 1.2s
57:	learn: 0.2141082	total: 510ms	remaining: 1.19s
58:	learn: 0.2134708	total: 519ms	remaining: 1.18s
59:	learn: 0.2123219	total: 528ms	remaining: 1.17s
60:	learn: 0.2102880	total: 537ms	remaining: 1.16s
61:	learn: 0.2095212	total: 546ms	remaining: 1.15s
62:	learn: 0.2083516	total: 555ms	

22:	learn: 0.2757315	total: 212ms	remaining: 1.56s
23:	learn: 0.2722967	total: 220ms	remaining: 1.55s
24:	learn: 0.2666697	total: 229ms	remaining: 1.54s
25:	learn: 0.2637751	total: 237ms	remaining: 1.52s
26:	learn: 0.2627532	total: 246ms	remaining: 1.51s
27:	learn: 0.2605824	total: 254ms	remaining: 1.5s
28:	learn: 0.2584334	total: 263ms	remaining: 1.49s
29:	learn: 0.2552505	total: 272ms	remaining: 1.48s
30:	learn: 0.2534032	total: 281ms	remaining: 1.47s
31:	learn: 0.2522467	total: 289ms	remaining: 1.46s
32:	learn: 0.2501915	total: 298ms	remaining: 1.45s
33:	learn: 0.2478272	total: 307ms	remaining: 1.44s
34:	learn: 0.2456822	total: 316ms	remaining: 1.43s
35:	learn: 0.2444360	total: 324ms	remaining: 1.41s
36:	learn: 0.2432587	total: 333ms	remaining: 1.4s
37:	learn: 0.2417493	total: 341ms	remaining: 1.39s
38:	learn: 0.2398695	total: 350ms	remaining: 1.38s
39:	learn: 0.2375509	total: 359ms	remaining: 1.37s
40:	learn: 0.2358815	total: 368ms	remaining: 1.36s
41:	learn: 0.2346135	total: 377ms

0:	learn: 0.4665638	total: 25.1ms	remaining: 4.82s
1:	learn: 0.4198040	total: 34.3ms	remaining: 3.28s
2:	learn: 0.4012277	total: 43.4ms	remaining: 2.75s
3:	learn: 0.3943937	total: 53ms	remaining: 2.5s
4:	learn: 0.3849069	total: 62.4ms	remaining: 2.35s
5:	learn: 0.3801985	total: 71ms	remaining: 2.21s
6:	learn: 0.3759254	total: 80ms	remaining: 2.13s
7:	learn: 0.3719280	total: 89.3ms	remaining: 2.06s
8:	learn: 0.3570804	total: 99.3ms	remaining: 2.03s
9:	learn: 0.3529627	total: 109ms	remaining: 1.99s
10:	learn: 0.3398887	total: 119ms	remaining: 1.96s
11:	learn: 0.3363768	total: 128ms	remaining: 1.94s
12:	learn: 0.3273592	total: 138ms	remaining: 1.91s
13:	learn: 0.3231605	total: 147ms	remaining: 1.88s
14:	learn: 0.3193891	total: 156ms	remaining: 1.85s
15:	learn: 0.3124823	total: 165ms	remaining: 1.82s
16:	learn: 0.3075170	total: 174ms	remaining: 1.8s
17:	learn: 0.3030987	total: 182ms	remaining: 1.77s
18:	learn: 0.2992994	total: 192ms	remaining: 1.75s
19:	learn: 0.2930130	total: 200ms	remain

166:	learn: 0.1625516	total: 1.5s	remaining: 234ms
167:	learn: 0.1624324	total: 1.51s	remaining: 225ms
168:	learn: 0.1621135	total: 1.52s	remaining: 216ms
169:	learn: 0.1617372	total: 1.53s	remaining: 207ms
170:	learn: 0.1613275	total: 1.54s	remaining: 198ms
171:	learn: 0.1608982	total: 1.55s	remaining: 189ms
172:	learn: 0.1607265	total: 1.56s	remaining: 180ms
173:	learn: 0.1605239	total: 1.56s	remaining: 171ms
174:	learn: 0.1602800	total: 1.57s	remaining: 162ms
175:	learn: 0.1600120	total: 1.58s	remaining: 153ms
176:	learn: 0.1597358	total: 1.59s	remaining: 144ms
177:	learn: 0.1594142	total: 1.6s	remaining: 135ms
178:	learn: 0.1590027	total: 1.61s	remaining: 126ms
179:	learn: 0.1586775	total: 1.62s	remaining: 117ms
180:	learn: 0.1583048	total: 1.63s	remaining: 108ms
181:	learn: 0.1580979	total: 1.64s	remaining: 98.8ms
182:	learn: 0.1577936	total: 1.64s	remaining: 89.8ms
183:	learn: 0.1575212	total: 1.65s	remaining: 80.8ms
184:	learn: 0.1573395	total: 1.66s	remaining: 71.8ms
185:	learn

151:	learn: 0.1661168	total: 1.33s	remaining: 359ms
152:	learn: 0.1658349	total: 1.34s	remaining: 350ms
153:	learn: 0.1655946	total: 1.35s	remaining: 342ms
154:	learn: 0.1654303	total: 1.36s	remaining: 333ms
155:	learn: 0.1650692	total: 1.37s	remaining: 324ms
156:	learn: 0.1648509	total: 1.37s	remaining: 315ms
157:	learn: 0.1644429	total: 1.38s	remaining: 306ms
158:	learn: 0.1640781	total: 1.39s	remaining: 298ms
159:	learn: 0.1638381	total: 1.4s	remaining: 289ms
160:	learn: 0.1636127	total: 1.41s	remaining: 280ms
161:	learn: 0.1632631	total: 1.42s	remaining: 271ms
162:	learn: 0.1629240	total: 1.43s	remaining: 263ms
163:	learn: 0.1627189	total: 1.44s	remaining: 254ms
164:	learn: 0.1623615	total: 1.44s	remaining: 245ms
165:	learn: 0.1620957	total: 1.45s	remaining: 236ms
166:	learn: 0.1617705	total: 1.46s	remaining: 228ms
167:	learn: 0.1615850	total: 1.47s	remaining: 219ms
168:	learn: 0.1613134	total: 1.48s	remaining: 210ms
169:	learn: 0.1608710	total: 1.49s	remaining: 201ms
170:	learn: 0

In [96]:
m_scores = pd.DataFrame(model_scores).round(4)
m_scores

Model Name  Accuracy train  \
0                                  LogisticRegression        0.819900   
1                              DecisionTreeClassifier        0.811700   
2                              RandomForestClassifier        0.825000   
3                                          GaussianNB        0.791100   
4                                         BernoulliNB        0.819500   
5                                  AdaBoostClassifier        0.201900   
6                          GradientBoostingClassifier        0.276200   
7                                       XGBClassifier        0.754400   
8   <catboost.core.CatBoostClassifier object at 0x...        0.859400   
9                                      LGBMClassifier        0.574300   
10                               KNeighborsClassifier        0.850200   
11                           LogisticRegression SMOTE        0.674800   
12                       DecisionTreeClassifier SMOTE        0.621900   
13                       RandomForestClassifier SMOTE        0.682200   
14                                   GaussianNB SMOTE        0.649400   
15                                  BernoulliNB SMOTE        0.666600   
16                           AdaBoostClassifier SMOTE        0.325500   
17                   GradientBoostingClassifier SMOTE        0.519200   
18                                XGBClassifier SMOTE        0.678900   
19  <catboost.core.CatBoostClassifier object at 0x...        0.896400   
20                               LGBMClassifier SMOTE        0.446600   
21                         KNeighborsClassifier SMOTE        0.846600   
22                          LogisticRegression ADASYN        0.646700   
23                      DecisionTreeClassifier ADASYN        0.568200   
24                      RandomForestClassifier ADASYN        0.681900   
25                                  GaussianNB ADASYN        0.580200   
26                                 BernoulliNB ADASYN        0.647000   
27                          AdaBoostClassifier ADASYN        0.322800   
28                  GradientBoostingClassifier ADASYN        0.642400   
29                               XGBClassifier ADASYN        0.592300   
30  <catboost.core.CatBoostClassifier object at 0x...        0.895900   
31                              LGBMClassifier ADASYN        0.512200   
32                        KNeighborsClassifier ADASYN        0.834400   
33                             LogisticRegression ENN        0.798200   
34                         DecisionTreeClassifier ENN        0.697100   
35                         RandomForestClassifier ENN        0.797700   
36                                     GaussianNB ENN        0.765200   
37                                    BernoulliNB ENN        0.780900   
38                             AdaBoostClassifier ENN        0.219400   
39                     GradientBoostingClassifier ENN        0.579900   
40                                  XGBClassifier ENN        0.794500   
41  <catboost.core.CatBoostClassifier object at 0x...        0.965500   
42                                 LGBMClassifier ENN        0.502000   
43                           KNeighborsClassifier ENN        0.976300   
44                     LogisticRegression SMOTE + ENN        0.750600   
45                 DecisionTreeClassifier SMOTE + ENN        0.753600   
46                 RandomForestClassifier SMOTE + ENN        0.753600   
47                             GaussianNB SMOTE + ENN        0.713700   
48                            BernoulliNB SMOTE + ENN        0.739200   
49                     AdaBoostClassifier SMOTE + ENN        0.246400   
50             GradientBoostingClassifier SMOTE + ENN        0.488100   
51                          XGBClassifier SMOTE + ENN        0.632300   
52  <catboost.core.CatBoostClassifier object at 0x...        0.942800   
53                         LGBMClassifier SMOTE + ENN        0.739300   
54                   KNeighb

In [99]:
mscore_sorted = m_scores.sort_values(by = ['F2 test'], ascending = False)
mscore_sorted

Model Name  Accuracy train  \
13                       RandomForestClassifier SMOTE        0.682200   
35                         RandomForestClassifier ENN        0.797700   
18                                XGBClassifier SMOTE        0.678900   
24                      RandomForestClassifier ADASYN        0.681900   
28                  GradientBoostingClassifier ADASYN        0.642400   
9                                      LGBMClassifier        0.574300   
26                                 BernoulliNB ADASYN        0.647000   
29                               XGBClassifier ADASYN        0.592300   
22                          LogisticRegression ADASYN        0.646700   
5                                  AdaBoostClassifier        0.201900   
31                              LGBMClassifier ADASYN        0.512200   
25                                  GaussianNB ADASYN        0.580200   
40                                  XGBClassifier ENN        0.794500   
33                             LogisticRegression ENN        0.798200   
36                                     GaussianNB ENN        0.765200   
14                                   GaussianNB SMOTE        0.649400   
37                                    BernoulliNB ENN        0.780900   
11                           LogisticRegression SMOTE        0.674800   
15                                  BernoulliNB SMOTE        0.666600   
43                           KNeighborsClassifier ENN        0.976300   
17                   GradientBoostingClassifier SMOTE        0.519200   
6                          GradientBoostingClassifier        0.276200   
32                        KNeighborsClassifier ADASYN        0.834400   
41  <catboost.core.CatBoostClassifier object at 0x...        0.965500   
21                         KNeighborsClassifier SMOTE        0.846600   
39                     GradientBoostingClassifier ENN        0.579900   
47                             GaussianNB SMOTE + ENN        0.713700   
49                     AdaBoostClassifier SMOTE + ENN        0.246400   
48                            BernoulliNB SMOTE + ENN        0.739200   
7                                       XGBClassifier        0.754400   
44                     LogisticRegression SMOTE + ENN        0.750600   
54                   KNeighborsClassifier SMOTE + ENN        0.923300   
19  <catboost.core.CatBoostClassifier object at 0x...        0.896400   
12                       DecisionTreeClassifier SMOTE        0.621900   
46                 RandomForestClassifier SMOTE + ENN        0.753600   
45                 DecisionTreeClassifier SMOTE + ENN        0.753600   
1                              DecisionTreeClassifier        0.811700   
34                         DecisionTreeClassifier ENN        0.697100   
23                      DecisionTreeClassifier ADASYN        0.568200   
30  <catboost.core.CatBoostClassifier object at 0x...        0.895900   
20                               LGBMClassifier SMOTE        0.446600   
3                                          GaussianNB        0.791100   
10                               KNeighborsClassifier        0.850200   
8   <catboost.core.CatBoostClassifier object at 0x...        0.859400   
50             GradientBoostingClassifier SMOTE + ENN        0.488100   
52  <catboost.core.CatBoostClassifier object at 0x...        0.942800   
2                              RandomForestClassifier        0.825000   
53                         LGBMClassifier SMOTE + ENN        0.739300   
4                                         BernoulliNB        0.819500   
51                          XGBClassifier SMOTE + ENN        0.632300   
0                                  LogisticRegression        0.819900   
38                             AdaBoostClassifier ENN        0.219400   
16                           AdaBoostClassifier SMOTE        0.325500   
27                          AdaBoostClassifier ADASYN        0.322800   
42                          

if precision low it means that the patients who has come for the appointment are predicted as they will not show up for the appointment. If recall is low it will mean that the patients who did not show up for the appointment is predicted as they will show up for the appointment. So we need to choose a model which for which both precision and recall are balanced with high model preformance score.

In [98]:
pd.DataFrame(model_scores).round(4).to_csv('tuned_models_Final.csv', index = False)

In [100]:
mscore_sorted.to_csv('tuned_models_Final_sorted.csv', index = False)